Высоцкий Степан, Устинова Мария, Ремизова Татьяна

В данной работе сначала происходил подбор параметров на нашем подгшотовленном датасете, далее мы взяли предложенный датасет итоговый и тюнили модели на нем. Так, сначала мы тестировали модели со старым тюнингом - модели обучались также стабильно и на новом датасете.

Пайплайн работы устроен достаточно простым образом: данные загружаются и подготавливаются в классе подбора фичей дополнительно, также мы заранее ресемплим выборку при помощи SMOTE для качественного обучения.

Далее мы подбирали параметры при помощи триалов в Optuna, после подбора мы тестируем их на всей выборке (тренируем на подмножестве и делаем оценку). А также запускаем модели на тестовом множестве для оценки на LB Kaggle.

Контроль переобучения можно провести на таблице ошибок, которая приводистя при каждой итерации оптимизации в Optuna. Переобучения не наблюдается на наших лучших моделях, об этом говорит и скор на отложенном тесте.

In [ ]:
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
from matplotlib import cm,colors


import pandas as pd
import seaborn as sns
from sklearn.ensemble import RandomForestClassifier, BaggingClassifier, GradientBoostingClassifier, AdaBoostClassifier, StackingClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, f1_score, precision_score, recall_score, balanced_accuracy_score, roc_auc_score
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression

import os
import optuna
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, roc_auc_score, confusion_matrix
from sklearn.preprocessing import StandardScaler

In [ ]:
pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 386.6/386.6 kB 13.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 242.5/242.5 kB 23.4 MB/s eta 0:00:00


In [ ]:
import os
import optuna
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, roc_auc_score, confusion_matrix
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.utils import to_categorical

In [ ]:
from imblearn.over_sampling import SMOTE

In [ ]:
df = pd.read_csv('https://raw.githubusercontent.com/stepikVys/gamma_knife/refs/heads/main/norm_and_ohe_dataset_with_diagnosis.csv', index_col='Unnamed: 0')
# Датасет подготовлен в прошлом домашнем задании.

In [ ]:
df.head()

Прогрессия  Пол  Диагноз  Число очагов  Объем очагов  Число фракций  \
0         1.0  1.0     0.75      0.041667      0.177158            0.0   
1         1.0  1.0     0.75      0.333333      0.010791            0.0   
2         1.0  0.0     1.00      0.083333      0.112410            0.0   
4         1.0  1.0     1.00      0.041667      0.049685            0.6   
5         1.0  0.0     1.00      0.583333      0.216052            0.0   

   Индекс Карновского  Лекарственное лечение  ОВГМ  Операция   Возраст  \
0            0.833333               0.333333   1.0       0.0  0.381818   
1            0.833333               1.000000   0.0       0.0  0.818182   
2            0.833333               0.666667   0.0       0.0  0.854545   
4            0.833333               0.333333   0.0       1.0  0.745455   
5            0.333333               0.333333   0.0       0.0  0.472727   

   Время реагирования  Время метастазирования  \
0           -0.005626                  8310.0   
1            0.099859                  8157.0   
2            0.057665                  7125.0   
4           -0.015471                  5060.0   
5            0.019691                  5144.0   

   Экстракраниальные метастазы_есть  Экстракраниальные метастазы_не известно  \
0                              True                                    False   
1                             False                                     True   
2                              True                                    False   
4                              True                                    False   
5                             False                                     True   

   Экстракраниальные метастазы_нет  Активирующие мутации_есть  \
0                            False                      False   
1                            False                      False   
2                            False                      False   
4                            False                      False   
5                            False                      False   

   Активирующие мутации_не известно  Активирующие мутации_нет  \
0                              True                     False   
1                             False                      True   
2                              True                     False   
4                              True                     False   
5                              True                     False   

  Онкологический диагноз  
0                    РМЖ  
1                    РМЖ  
2                     РП  
4                     РП  
5                     РП

In [ ]:
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
tf.get_logger().setLevel('INFO')

In [ ]:
# get directories
filepath = '/content'
transgenic_data = df
results_path = filepath + '/results'

In [ ]:
import os
import numpy as np
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'


def convertToOneHot(vector, num_classes=None):
    """
    Converts an input 1-D vector of integers into an output
    2-D array of one-hot vectors, where an i'th input value
    of j will set a '1' in the i'th row, j'th column of the
    output array.
    Example:
        v = np.array((1, 0, 4))
        one_hot_v = convertToOneHot(v)
        print one_hot_v
        [[0 1 0 0 0]
         [1 0 0 0 0]
         [0 0 0 0 1]]
    """

    assert isinstance(vector, np.ndarray)
    assert len(vector) > 0

    if num_classes is None:
        num_classes = np.max(vector) + 1
    else:
        assert num_classes > 0
        assert num_classes >= np.max(vector)

    result = np.zeros(shape=(len(vector), num_classes))
    result[np.arange(len(vector)), vector] = 1
    return result.astype(int)


# Dataset class: adapted from TensorFlow source example:
# https://github.com/tensorflow/tensorflow/blob/master/tensorflow/contrib/learn/python/learn/datasets/mnist.py
def _to_tensor(x, dtype):
    """Convert the input `x` to a tensor of type `dtype`.
    # Arguments
        x: An object to be converted (numpy array, list, tensors).
        dtype: The destination type.
    # Returns
        A tensor.
    """
    return tf.convert_to_tensor(x, dtype=dtype)


# add a second data label: meta (Z), with the same usage as labels (y)
class DataSet_meta:
    """Base data set class
    """

    def __init__(self, shuffle=True, labeled=True, **data_dict):
        assert '_data' in data_dict
        if labeled:
            assert '_labels' in data_dict
            assert data_dict['_data'].shape[0] == data_dict['_labels'].shape[0]
            assert data_dict['_data'].shape[0] == data_dict['_meta'].shape[0]
        self._labeled = labeled
        self._shuffle = shuffle
        self.__dict__.update(data_dict)
        self._num_samples = self._data.shape[0]
        self._index_in_epoch = 0
        if self._shuffle:
            self._shuffle_data()

    def __len__(self):
        return len(self._data)

    @property
    def index_in_epoch(self):
        return self._index_in_epoch

    @property
    def num_samples(self):
        return self._num_samples

    @property
    def data(self):
        return self._data

    @property
    def labels(self):
        return self._labels

    @property
    def meta(self):
        return self._meta

    @property
    def labeled(self):
        return self._labeled

    @property
    def valid_data(self):
        return self._valid_data

    @property
    def valid_labels(self):
        return self._valid_labels

    @property
    def valid_meta(self):
        return self._valid_meta

    @property
    def test_data(self):
        return self._test_data

    @property
    def test_labels(self):
        return self._test_labels

    @property
    def test_meta(self):
        return self._test_meta

    @classmethod
    def load(cls, filename):
        data_dict = np.load(filename)
        return cls(**data_dict)

    def save(self, filename):
        data_dict = self.__dict__
        np.savez_compressed(filename, **data_dict)

    def _shuffle_data(self):
        shuffled_idx = np.arange(self._num_samples)
        np.random.shuffle(shuffled_idx)
        self._data = self._data[shuffled_idx]
        if self._labeled:
            self._labels = self._labels[shuffled_idx]
            self._meta = self._meta[shuffled_idx]

    def next_batch(self, batch_size):
        assert batch_size <= self._num_samples
        start = self._index_in_epoch
        if start + batch_size > self._num_samples:
            data_batch = self._data[start:]
            if self._labeled:
                labels_batch = self._labels[start:]
                meta_batch = self._meta[start:]
            remaining = batch_size - (self._num_samples - start)
            if self._shuffle:
                self._shuffle_data()
            start = 0
            data_batch = np.concatenate([data_batch, self._data[:remaining]],
                                        axis=0)
            if self._labeled:
                labels_batch = np.concatenate([labels_batch,
                                               self._labels[:remaining]],
                                              axis=0)
                meta_batch = np.concatenate([meta_batch,
                                             self._meta[:remaining]],
                                            axis=0)
            self._index_in_epoch = remaining
        else:
            data_batch = self._data[start:start + batch_size]
            if self._labeled:
                labels_batch = self._labels[start:start + batch_size]
                meta_batch = self._meta[start:start + batch_size]
            self._index_in_epoch = start + batch_size
        batch = (data_batch, labels_batch, meta_batch) if self._labeled else data_batch
        return batch


def squared_distance(X):
    '''
    Calculates the squared Euclidean distance matrix.
    X:              an n-by-p matrix, which includes n samples in dimension p
    returns:        n x n pairwise squared Euclidean distance matrix
    '''

    r = tf.reduce_sum(X * X, 1)
    r = tf.reshape(r, [-1, 1])
    D = r - 2 * tf.matmul(X, X, transpose_b=True) + tf.transpose(r)
    return D


class Model(object):
    def __init__(self,
                 input_node,
                 hidden_layers_node,
                 output_node,
                 gating_net_hidden_layers_node,
                 display_step,
                 activation_gating,
                 activation_pred,
                 feature_selection=True,
                 batch_normalization=False,  # NB Attention! batchnorm is False
                 a=1,
                 sigma=0.5,
                 lam=0.5,
                 gamma1=0,
                 gamma2=0,
                 num_meta_label=None,
                 stddev_input=0.1,
                 stddev_input_gates=0.1,
                 seed=1,
                 ):
        """ LSPIN Model
        # Arguments:
            input_node: integer, input dimension of the prediction network
            hidden_layers_node: list, number of nodes for each hidden layer for the prediction net, example: [200,200]
            output_node: integer, number of nodes for the output layer of the prediction net, 1 (regression) or 2 (classification)
            gating_net_hidden_layers_node: list, number of nodes for each hidden layer of the gating net, example: [200,200]
            display_step: integer, number of epochs to output info
            activation_gating: string, activation function of the gating net: 'relu', 'l_relu', 'sigmoid', 'tanh', or 'none'
            activation_pred: string, activation function of the prediction net: 'relu', 'l_relu', 'sigmoid', 'tanh', or 'none'
            feature_selection: bool, if using the gating net
            a: float,
            sigma: float, std of the gaussion reparameterization noise
            lam: float, regularization parameter (lambda_1) of the L0 penalty
            gamma1: float, regularization parameter (lambda_2) to encourage similar samples select similar features
            gamma2: float, variant of lambda2, to encourage disimilar samples select disimilar features
            num_meta_label: integer, the number of group labels when computing the second regularization term
            stddev_input: float, std of the normal initializer for the prediction network weights
            stddev_input_gates: float, std of the normal initializer for the gating network weights
            seed: integer, random seed
        """

        # Register hyperparameters of LSPIN
        self.a = a
        self.sigma = sigma
        self.lam = lam

        self._activation_gating = activation_gating
        self.activation_gating = activation_gating  # will overwrite _activation_gating

        self._activation_pred = activation_pred
        self.activation_pred = activation_pred  # will overwrite _activation_pred

        # Register hyperparameters for training

        # self._batch_size = batch_size
        self.display_step = display_step

        # 2nd regularization parameter for the similarity penalty
        self.gamma1 = gamma1
        self.gamma2 = gamma2

        G = tf.Graph()
        with G.as_default():
            self.sess = tf.Session(graph=G)
            # tf Graph Input
            X = tf.placeholder(tf.float32, [None, input_node])  # X.shape == [batch_size, feature_size]
            y = tf.placeholder(tf.float32, [None, output_node])

            train_gates = tf.placeholder(tf.float32, [1], name='train_gates')

            # add a second layer of labels to apply penalty
            Z = tf.placeholder(tf.float32, [None, num_meta_label])

            is_train = tf.placeholder(tf.bool, [], name='is_train')  # for batch normalization

            self.learning_rate = tf.placeholder(tf.float32, shape=[], name='learning_rate')

            self.compute_sim = tf.placeholder(tf.bool, [],
                                              name='compute_sim')  # whether to compute the 2nd penalty term or not

            self.gatesweights = []
            nnweights = []
            prev_node = input_node
            prev_x = X

            # Gating network
            if feature_selection:
                for i in range(len(gating_net_hidden_layers_node)):
                    gates_layer_name = 'gate_layer' + str(i + 1)

                    with tf.variable_scope(gates_layer_name, reuse=tf.AUTO_REUSE):
                        weights = tf.get_variable('weights', [prev_node, gating_net_hidden_layers_node[i]],
                                                  initializer=tf.truncated_normal_initializer(
                                                      stddev=stddev_input_gates))
                        biases = tf.get_variable('biases', [gating_net_hidden_layers_node[i]],
                                                 initializer=tf.constant_initializer(0.0))

                        self.gatesweights.append(weights)
                        self.gatesweights.append(biases)

                        gates_layer_out = self.activation_gating(tf.matmul(prev_x, weights) + biases)

                        prev_node = gating_net_hidden_layers_node[i]
                        prev_x = gates_layer_out
                weights2 = tf.get_variable('weights2', [prev_node, input_node],
                                           initializer=tf.truncated_normal_initializer(stddev=stddev_input_gates))
                biases2 = tf.get_variable('biases2', [input_node],
                                          initializer=tf.constant_initializer(0.0))

                self.gatesweights.append(weights2)
                self.gatesweights.append(biases2)
                self.alpha = self.activation_gating(tf.matmul(prev_x, weights2) + biases2)
                prev_x = X
                self.stochastic_gates = self.get_stochastic_gate_train(prev_x, train_gates)
                prev_x = prev_x * self.stochastic_gates
                # prev_x = self.feature_selector(prev_x, train_gates)
                prev_node = input_node

            # Prediction network
            layer_name = 'layer' + str(1)
            for i in range(len(hidden_layers_node)):
                layer_name = 'layer' + str(i + 1)
                with tf.variable_scope(layer_name, reuse=tf.AUTO_REUSE):
                    weights = tf.get_variable('weights', [prev_node, hidden_layers_node[i]],
                                              initializer=tf.truncated_normal_initializer(stddev=stddev_input))
                    nnweights.append(weights)
                    biases = tf.get_variable('biases', [hidden_layers_node[i]],
                                             initializer=tf.constant_initializer(0.0))
                    nnweights.append(biases)
                    if batch_normalization:
                        prev_x = tf.layers.batch_normalization(prev_x, training=is_train)
                    layer_out = self.activation_pred(tf.matmul(prev_x, weights) + biases)

                    prev_node = hidden_layers_node[i]
                    prev_x = layer_out

            # Output of model
            # Minimize error using cross entropy
            if output_node == 1:

                weights = tf.get_variable('weights', [prev_node, 1],
                                          initializer=tf.truncated_normal_initializer(stddev=stddev_input))
                nnweights.append(weights)
                biases = tf.get_variable('biases', [1],
                                         initializer=tf.constant_initializer(0.0))
                nnweights.append(biases)
                if batch_normalization:
                    layer_out = tf.layers.batch_normalization(layer_out, training=is_train)
                pred = (tf.matmul(layer_out, weights) + biases)
                loss_fun = tf.reduce_mean(tf.squared_difference(pred, y))
                pred_log = (layer_out)
            else:

                weights = tf.get_variable('weights', [prev_node, output_node],
                                          initializer=tf.truncated_normal_initializer(stddev=stddev_input))
                nnweights.append(weights)
                biases = tf.get_variable('biases', [output_node],
                                         initializer=tf.constant_initializer(0.0))
                nnweights.append(biases)

                if batch_normalization:
                    prev_x = tf.layers.batch_normalization(prev_x, training=is_train)
                layer_out = self.activation_pred(tf.matmul(prev_x, weights) + biases)

                prev_node = output_node
                prev_x = layer_out

                pred = tf.nn.softmax(layer_out)
                pred_log = (layer_out)
                loss_fun = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y, logits=layer_out))

            if feature_selection:
                # gates regularization
                input2cdf = self.alpha

                reg = 0.5 - 0.5 * tf.erf((-1 / (2 * self.a) - input2cdf) / (self.sigma * np.sqrt(2)))

                reg_gates = self.lam * tf.reduce_mean(tf.reduce_mean(reg, axis=-1))

                # 2nd regularization penalty
                # to force samples of the same labels to select similar features

                # New feature: reg_sim is only open when the compute_sim flag is true
                # if self.compute_sim:
                # squared distance between the labels can be either 0 or 2,
                # scale the corresponding affinity (K_batch) to 1 or 0.
                # K_batch = 1.0 - squared_distance(Z)/2.0

                # euclidean distance matrix of the gate matrix
                # D_batch = squared_distance(self.stochastic_gates)

                # element-wise multiplication
                # reg_sim = self.gamma1*tf.reduce_mean(tf.reduce_mean(tf.multiply(K_batch,D_batch),axis=-1))+ \
                #          self.gamma2*tf.reduce_mean(tf.reduce_mean(tf.multiply((1.0 - K_batch),-D_batch)))

                # else:
                # reg_sim = tf.constant(0.)

                reg_sim = tf.cond(self.compute_sim,
                                  lambda: self.gamma1 * tf.reduce_mean(tf.reduce_mean(
                                      tf.multiply((1.0 - squared_distance(Z) / 2.0),
                                                  squared_distance(self.stochastic_gates)), axis=-1)) +
                                          self.gamma2 * tf.reduce_mean(tf.reduce_mean(
                                      tf.multiply(squared_distance(Z) / 2.0, -squared_distance(self.stochastic_gates)),
                                      axis=1)),
                                  lambda: tf.constant(0.))

                loss = loss_fun + reg_gates + reg_sim


            else:
                loss = loss_fun
                reg_gates = tf.constant(0.)
                reg_sim = tf.constant(0.)
            # Get Optimizer
            if batch_normalization:
                update_ops = tf.get_collection(tf.GraphKeys.UPDATE_OPS)
                with tf.control_dependencies(update_ops):
                    train_step = tf.train.GradientDescentOptimizer(self.learning_rate).minimize(loss)
            else:
                train_step = tf.train.GradientDescentOptimizer(self.learning_rate).minimize(loss)
            # For evaluation
            correct_prediction = tf.equal(tf.argmax(pred, 1), tf.argmax(y, 1))
            accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
            # Initialize the variables (i.e. assign their default value)
            init_op = tf.global_variables_initializer()
            self.saver = tf.train.Saver()

        # Save into class members
        self.X = X
        self.y = y
        self.Z = Z
        # self.K_batch = K_batch
        self.pred = pred
        self.train_gates = train_gates
        self.is_train = is_train
        self.loss = loss
        self.reg_gates = reg_gates
        self.reg_sim = reg_sim
        self.pred_log = pred_log
        self.train_step = train_step
        self.correct_prediction = correct_prediction
        self.accuracy = accuracy
        self.output_node = output_node
        self.nnweights = nnweights.copy()
        self.weights = weights
        self.biases = biases
        # set random state
        tf.set_random_seed(seed)
        self.sess.run(init_op)

    # @property
    # def batch_size(self):
    # return self._batch_size

    # @batch_size.setter
    # def batch_size(self,value):
    # self._batch_size=value

    @property
    def activation_gating(self):
        return self._activation_gating

    @activation_gating.setter
    def activation_gating(self, value):
        if value == 'relu':
            self._activation_gating = tf.nn.relu
        elif value == 'l_relu':
            self._activation_gating = tf.nn.leaky_relu
        elif value == 'sigmoid':
            self._activation_gating = tf.nn.sigmoid
        elif value == 'tanh':
            self._activation_gating = tf.nn.tanh
        elif value == 'none':
            self._activation_gating = lambda x: x
        else:
            raise NotImplementedError('activation for the gating network not recognized')

    @property
    def activation_pred(self):
        return self._activation_pred

    @activation_pred.setter
    def activation_pred(self, value):
        if value == 'relu':
            self._activation_pred = tf.nn.relu
        elif value == 'l_relu':
            self._activation_pred = tf.nn.leaky_relu
        elif value == 'sigmoid':
            self._activation_pred = tf.nn.sigmoid
        elif value == 'tanh':
            self._activation_pred = tf.nn.tanh
        elif value == 'none':
            self._activation_pred = lambda x: x
        else:
            raise NotImplementedError('activation for the prediction network not recognized')

    def _to_tensor(self, x, dtype):
        """Convert the input `x` to a tensor of type `dtype`.
        # Arguments
            x: An object to be converted (numpy array, list, tensors).
            dtype: The destination type.
        # Returns
            A tensor.
        """
        return tf.convert_to_tensor(x, dtype=dtype)

    def get_weights(self):
        """
        Get network weights
        """
        weights_out = self.sess.run(self.nnweights, feed_dict={self.is_train: False})
        biases_out = self.sess.run(self.biases, feed_dict={self.is_train: False})
        return weights_out

    def hard_sigmoid(self, x, a):
        """Segment-wise linear approximation of sigmoid.
        Faster than sigmoid.
        Returns `0.` if `x < -2.5`, `1.` if `x > 2.5`.
        In `-2.5 <= x <= 2.5`, returns `0.2 * x + 0.5`.
        # Arguments
            x: A tensor or variable.
        # Returns
            A tensor.
        """
        x = a * x + 0.5
        zero = self._to_tensor(0., x.dtype.base_dtype)
        one = self._to_tensor(1., x.dtype.base_dtype)
        x = tf.clip_by_value(x, zero, one)
        return x

    def get_stochastic_gate_train(self, prev_x, train_gates):
        """
        This function replaced the feature_selector function in order to save Z
        """
        # gaussian reparametrization
        base_noise = tf.random_normal(shape=tf.shape(prev_x), mean=0., stddev=1.)

        z = self.alpha + self.sigma * base_noise * train_gates
        stochastic_gate = self.hard_sigmoid(z, self.a)

        return stochastic_gate

    def eval(self, new_X, new_y, new_Z, compute_sim):
        """
        Evaluate the accuracy and loss
        """

        acc, loss = self.sess.run([self.accuracy, self.loss], feed_dict={self.X: new_X,
                                                                         self.y: new_y,
                                                                         self.Z: new_Z,
                                                                         self.train_gates: [0.0],
                                                                         self.is_train: False,
                                                                         self.compute_sim: compute_sim,
                                                                         })
        return np.squeeze(acc), np.squeeze(loss)

    def get_raw_alpha(self, X_in):
        """
        evaluate the learned parameter for stochastic gates
        """
        dp_alpha = self.sess.run(self.alpha, feed_dict={self.X: X_in, self.is_train: False, })
        return dp_alpha

    def get_prob_alpha(self, X_in):
        """
        convert the raw alpha into the actual probability
        """
        dp_alpha = self.get_raw_alpha(X_in)
        prob_gate = self.compute_learned_prob(dp_alpha)
        return prob_gate

    def hard_sigmoid_np(self, x, a):
        return np.minimum(1, np.maximum(0, a * x + 0.5))

    def compute_learned_prob(self, alpha):
        z = alpha
        stochastic_gate = self.hard_sigmoid_np(z, self.a)
        return stochastic_gate

    def load(self, model_path=None):
        if model_path == None:
            raise Exception()
        self.saver.restore(self.sess, model_path)

    def save(self, model_dir=None):
        if model_dir == None:
            raise Exception()
        try:
            os.mkdir(model_dir)
        except:
            pass
        model_file = model_dir + "/model"
        self.saver.save(self.sess, model_file)

    def train(self,
              dataset,
              batch_size,
              num_epoch=100,
              lr=0.1,
              compute_sim=False,
              ):

        train_losses, train_accuracies = [], []
        val_losses = []
        val_accuracies = []

        # record the sim reg loss per batch
        sim_reg_losses_per_b = []
        # record the network weights
        nnweights_list = []
        print("num_samples : {}".format(dataset.num_samples))
        for epoch in range(num_epoch):
            avg_loss = 0.
            total_batch = int(dataset.num_samples / batch_size)

            # Deprecated: the compute_sim flag is up for every compute_sim_step
            # compute_sim = not ((epoch+1) % compute_sim_step)

            # Loop over all batches
            for i in range(total_batch):
                batch_xs, batch_ys, batch_zs = dataset.next_batch(batch_size)

                # for the 2nd penalty, precompute the K matrix
                # TODO: make this squared_distance function consistent
                # (TODO: only compute it when feature_selection flag is on)
                # K_batch = 1.0 - squared_distance(self._to_tensor(batch_zs,dtype=tf.float32))/2.0
                # K_batch = 1.0 - distance_np(batch_zs)**2/2.0

                _, c = self.sess.run([self.train_step, self.loss], feed_dict={self.X: batch_xs,
                                                                              self.y: batch_ys,
                                                                              self.Z: batch_zs,
                                                                              self.learning_rate: lr,
                                                                              self.compute_sim: compute_sim,
                                                                              self.train_gates: [1.0],
                                                                              self.is_train: True,
                                                                              })

                # sim_reg_losses_per_b.append(reg_sim_fs)
                avg_loss += c / total_batch
            train_losses.append(avg_loss)
            # Display logs per epoch step
            if (epoch + 1) % self.display_step == 0:

                valid_acc, valid_loss = self.eval(dataset.valid_data, dataset.valid_labels, dataset.valid_meta,
                                                  compute_sim)
                val_accuracies.append(valid_acc)
                val_losses.append(valid_loss)
                # nnweights_list.append(nnweights_perE)
                if self.output_node != 1:
                    print("Epoch: {} train loss={:.9f} valid loss= {:.9f} valid acc= {:.9f}".format(epoch + 1, \
                                                                                                    avg_loss,
                                                                                                    valid_loss,
                                                                                                    valid_acc))
                else:
                    print("Epoch: {} train loss={:.9f} valid loss= {:.9f}".format(epoch + 1, \
                                                                                  avg_loss, valid_loss))
                # print("train reg_fs: {}".format(reg_fs))
                # print("train sim_penalty: {}".format(reg_sim_fs))
        print("Optimization Finished!")
        test_acc, test_loss = self.eval(dataset.test_data, dataset.test_labels, dataset.test_meta, compute_sim)
        print("test loss: {}, test acc: {}".format(test_loss, test_acc))
        self.acc = test_acc  # used for recording test acc for figures
        # self.sim_reg_losses_per_b = sim_reg_losses_per_b # used for recording training sim loss
        self.train_losses2plot = train_losses
        # self.nnweights_list = nnweights_list

        return train_accuracies, train_losses, val_accuracies, val_losses

    def test(self, X_test):
        """
        Predict on the test set
        """
        prediction = self.sess.run([self.pred],
                                   feed_dict={self.X: X_test, self.train_gates: [0.0], self.is_train: False, })
        if self.output_node != 1:
            prediction = np.argmax(prediction[0], axis=1)
        return prediction

    def evaluate(self, X, y, Z, compute_sim):
        """
        Get the test acc and loss
        """
        acc, loss = self.eval(X, y, Z, compute_sim)
        print("test loss: {}, test acc: {}".format(loss, acc))
        print("Saving model..")
        return acc, loss

    def get_KD(self, X, Z):

        K_batch_sim = 1.0 - squared_distance(self._to_tensor(Z, dtype=tf.float32)) / 2.0

        D_batch_sim = squared_distance(self._to_tensor(self.get_prob_alpha(X), dtype=tf.float32))

        K_batch_dis = squared_distance(self._to_tensor(Z, dtype=tf.float32)) / 2.0

        D_batch_dis = -squared_distance(self._to_tensor(self.get_prob_alpha(X), dtype=tf.float32))

        return K_batch_sim, D_batch_sim, K_batch_dis, D_batch_dis

Instructions for updating:
non-resource variables are not supported in the long term


In [ ]:
from tensorflow.keras.utils import to_categorical
import tensorflow as tf
import os

os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'


def get_device() -> str:
    """
    prints out your physical devices.
    The user determines which device to use GPU/CPU by input.
    :return: device to be used.
    """
    print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))
    gpus = tf.config.list_physical_devices('GPU')
    for gpu in gpus:
        print("Name:", gpu.name, "  Type:", gpu.device_type)
    print("Num CPUs Available: ", len(tf.config.list_physical_devices('CPU')))

    cpus = tf.config.list_physical_devices('CPU')
    for cpu in cpus:
        print("Name:", cpu.name, "  Type:", cpu.device_type)

    device = input("Enter device (such as /device:GPU:0 or /device:CPU:0): ")
    return device

In [ ]:
smote = SMOTE(random_state=42)
x, y = smote.fit_resample(transgenic_data[['Пол', 'Диагноз', 'Число очагов', 'Объем очагов',
       'Число фракций', 'Индекс Карновского', 'Лекарственное лечение', 'ОВГМ',
       'Операция', 'Возраст', 'Время реагирования', 'Время метастазирования',
       'Экстракраниальные метастазы_есть',
       'Экстракраниальные метастазы_не известно',
       'Экстракраниальные метастазы_нет', 'Активирующие мутации_есть',
       'Активирующие мутации_не известно', 'Активирующие мутации_нет']], transgenic_data['Прогрессия'])

In [ ]:
new_trasngenic_data = pd.concat([x, y], axis=1)
new_trasngenic_data

Пол   Диагноз  Число очагов  Объем очагов  Число фракций  \
0    1.000000  0.750000      0.041667      0.177158            0.0   
1    1.000000  0.750000      0.333333      0.010791            0.0   
2    0.000000  1.000000      0.083333      0.112410            0.0   
3    1.000000  1.000000      0.041667      0.049685            0.6   
4    0.000000  1.000000      0.583333      0.216052            0.0   
..        ...       ...           ...           ...            ...   
697  1.000000  0.750000      0.055384      0.118100            0.0   
698  0.867072  0.683536      0.325152      0.206562            0.0   
699  0.000000  0.956620      0.003615      0.215157            0.0   
700  1.000000  0.627836      0.315808      0.297454            0.0   
701  0.498484  0.624621      0.166793      0.388789            0.0   

     Индекс Карновского  Лекарственное лечение      ОВГМ  Операция   Возраст  \
0              0.833333               0.333333  1.000000  0.000000  0.381818   
1              0.833333               1.000000  0.000000  0.000000  0.818182   
2              0.833333               0.666667  0.000000  0.000000  0.854545   
3              0.833333               0.333333  0.000000  1.000000  0.745455   
4              0.333333               0.333333  0.000000  0.000000  0.472727   
..                  ...                    ...       ...       ...       ...   
697            0.833333               0.396629  0.000000  0.810113  0.368928   
698            0.688821               0.710976  0.867072  0.132928  0.645099   
699            0.666667               0.333333  0.000000  0.000000  0.683769   
700            0.666667               0.837114  0.511342  0.000000  0.536570   
701            0.583586               0.832828  0.498484  0.000000  0.627411   

     Время реагирования  Время метастазирования  \
0             -0.005626             8310.000000   
1              0.099859             8157.000000   
2              0.057665             7125.000000   
3             -0.015471             5060.000000   
4              0.019691             5144.000000   
..                  ...                     ...   
697            0.469771             4203.274472   
698           -0.003319              296.196349   
699            0.021469                0.000000   
700            0.289406              745.659728   
701            0.009166              435.984837   

     Экстракраниальные метастазы_есть  \
0                                True   
1                               False   
2                                True   
3                                True   
4                               False   
..                                ...   
697                              True   
698                              True   
699                              True   
700                              True   
701                              True   

     Экстракраниальные метастазы_не известно  Экстракраниальные метастазы_нет  \
0                                      False                            False   
1                                       True                            False   
2                                      False                            False   
3                                      False                            False   
4                                       True                            False   
..                                       ...                              ...   
697                                     True                            False   
698                                     True                            False   
699                                    False                            False   
700                                    False                            False   
701                                    False                             True   

     Активирующие мутации_есть  Активирующие мутации_не известно  \
0                        False                              T

In [ ]:
transgenic_data.columns

Index(['Прогрессия', 'Пол', 'Диагноз', 'Число очагов', 'Объем очагов',
       'Число фракций', 'Индекс Карновского', 'Лекарственное лечение', 'ОВГМ',
       'Операция', 'Возраст', 'Время реагирования', 'Время метастазирования',
       'Экстракраниальные метастазы_есть',
       'Экстракраниальные метастазы_не известно',
       'Экстракраниальные метастазы_нет', 'Активирующие мутации_есть',
       'Активирующие мутации_не известно', 'Активирующие мутации_нет',
       'Онкологический диагноз'],
      dtype='object')

In [ ]:
smote = SMOTE(random_state=42)
X = pd.read_pickle('/content/features_dataset_normalized.pkl')
X_train_resampled_, y_train_resampled_ = smote.fit_resample(X.drop(columns='Прогрессия'), X['Прогрессия'])
X_test = pd.read_pickle('/content/test_dataset_normalized (1).pkl')

data_norm = pd.concat([X_train_resampled_, y_train_resampled_], axis=1)

In [ ]:
data_norm

Число очагов  Объем очагов  Число фракций  Индекс Карновского  ОВГМ  \
0        0.047619      0.177158            0.0            0.833333     1   
1        0.380952      0.010791            0.0            0.833333     0   
2        0.095238      0.112410            0.0            0.833333     0   
3        0.047619      0.049685            0.6            0.833333     0   
4        0.666667      0.216052            0.0            0.333333     0   
..            ...           ...            ...                 ...   ...   
731      0.002905      0.056477            0.0            0.676833     0   
732      0.045841      0.061195            0.0            0.827109     0   
733      0.156686      0.228403            0.0            0.666667     0   
734      0.085760      0.232430            0.0            0.666667     0   
735      0.000000      0.204782            0.0            0.500000     0   

     Операция   Возраст  Время метастазирования  Время реагирования  КРР  \
0           0  0.421053                1.164881           -0.005626    0   
1           0  0.842105                1.143593            0.099859    0   
2           0  0.877193                1.000000            0.057665    0   
3           1  0.771930                0.712676           -0.015471    0   
4           0  0.508772                0.724363            0.019691    0   
..        ...       ...                     ...                 ...  ...   
731         0  0.490158                0.211182            0.088418    0   
732         0  0.414648                0.057650            0.011853    0   
733         0  0.583189                0.229784            0.000521    0   
734         0  0.611957                0.150926            0.008499    0   
735         0  0.614324                0.092412            0.047708    0   

     Меланома  НМРЛ  РМЖ  РП  Таргетная терапия  Химиотерапия  Без лечения  \
0           0     0    1   0                  0             0            0   
1           0     0    1   0                  0             1            0   
2           0     0    0   1                  1             0            0   
3           0     0    0   1                  0             0            0   
4           0     0    0   1                  0             0            0   
..        ...   ...  ...  ..                ...           ...          ...   
731         0     0    1   0                  0             0            0   
732         0     1    0   0                  0             1            0   
733         0     0    1   0                  1             0            0   
734         0     1    0   0                  0             1            0   
735         1     0    0   0                  0             0            0   

     Мужчина  Прогрессия  
0          0           1  
1          0           1  
2          1           1  
3          0           1  
4          1           1  
..       ...         ...  
731        0           0  
732        1           0  
733        0           0  
734        0           0  
735        1           0  

[736 rows x 19 columns]

In [ ]:
X_test

Число очагов  Объем очагов  Число фракций  Индекс Карновского  ОВГМ  \
0         0.0000      0.580660       0.000000                 0.5     0   
1         0.3750      0.794049       0.000000                 1.0     1   
2         0.0000      0.000000       0.000000                 1.0     1   
3         0.4375      0.269177       0.000000                 1.0     0   
4         0.0625      0.037192       0.000000                 1.0     0   
5         0.5000      0.639238       0.000000                 1.0     1   
6         0.6875      0.225941       0.000000                 0.5     1   
7         0.0000      0.420735       0.000000                 0.5     0   
8         0.1250      0.120874       0.000000                 1.0     0   
9         0.0000      0.325430       0.000000                 1.5     0   
10        0.5000      0.499303       0.000000                 1.0     0   
11        0.0625      0.239424       0.000000                 0.5     0   
12        1.0000      1.000000       0.000000                 1.0     0   
13        0.0625      0.037657       0.000000                 1.5     0   
14        0.0000      0.129707       0.000000                 0.5     0   
15        0.0000      0.277545       0.000000                 1.0     0   
16        0.0000      0.866109       0.000000                 0.5     0   
17        0.0000      0.406323       0.000000                 1.0     0   
18        0.3750      0.384472       0.000000                 0.0     0   
19        0.1250      0.056718       0.000000                 0.5     0   
20        0.4375      0.712227       0.000000                 1.0     0   
21        0.0000      0.403068       0.000000                 0.5     0   
22        0.0000      0.132497       0.333333                 1.0     0   
23        0.4375      0.516969       0.333333                 0.5     0   
24        0.8750      0.561599       0.333333                 1.5     0   
25        0.6875      0.380288       0.000000                 0.5     1   
26        0.5000      0.081358       0.333333                 0.5     0   
27        0.0625      0.192934       0.333333                 1.0     0   
28        0.0000      0.062762       0.333333                 1.0     0   
29        0.1250      0.148303       0.000000                 0.5     0   
30        0.2500      0.004649       0.000000                 1.5     0   
31        1.0000      0.184100       0.333333                 1.5     0   
32        0.5625      0.617387       0.000000                 1.0     0   
33        0.8750      0.557880       0.333333                 1.5     0   
34        0.0000      0.013947       0.000000                 1.5     0   
35        0.0625      0.518364       0.333333                 1.0     0   
36        0.5000      0.212924       0.333333                 1.5     1   
37        0.1250      0.992562       0.333333                 1.0     0   
38        0.0000      0.076244       0.000000                 1.0     1   
39        0.7500      0.859135       0.666667                 1.0     0   
40        0.3125      0.078568       1.000000                 1.0     0   
41        0.0000      0.183636       0.000000                 1.0     0   
42        0.7500      0.358903       0.000000                 1.5     0   
43        0.6875      0.809391       0.333333                 1.5     1   

    Операция   Возраст  Время метастазирования  Время реагирования  ID  КРР  \
0          0  0.611111                0.535470            0.011524   1    1   
1          1  0.185185                0.101514            0.331626   2    0   
2          0  0.722222               -0.025230            0.275288   3    0   
3          0  0.777778                0.303057            0.008963   4    0   
4          0  0.851852                0.106857            0.007682   5    0   
5          0  0.481481                0.214604            0.361076   6    0   
6          0  0.740741                0.051054           -0.003841   7    1

In [ ]:
class LocallySparse:
    """
    uses the LSPIN model to classify transgenic targeting in mouse data.
    """
    def __init__(self, data: pd.DataFrame, n_classes: int) -> None:
        """
        :param data: raw dataframe of neuronal recordings.
        :param n_classes: number of transgenic lines in the dataframe.
        """
        self.data = data
        self.n_classes = n_classes
        self.model, self.best_model = None, None
        self.model_params, self.training_params, self.class_names = {}, {}, {}
        self.x_train, self.y_train, self.x_val, self.y_val, self.x_test, self.y_test = self._preprocess_data()

    def _preprocess_data(self) -> tuple:
        """
        :param df: raw dataframe to be processed.
        :param n_classes: number of classes in the dataframe.
        :return: split into train, validation and test.
        """
        db = self.data.dropna(axis=1, how='all')
        db = db.dropna(axis=0)


        # irrelevant_columns = ['Онкологический диагноз'] #уже удалено
        # db = db.drop([x for x in irrelevant_columns if x in db.columns], axis=1, errors='ignore')

        # db['Экстракраниальные метастазы_есть'] = db['Экстракраниальные метастазы_есть'].astype(int)
        # db['Экстракраниальные метастазы_не известно'] = db['Экстракраниальные метастазы_не известно'].astype(int)
        # db['Экстракраниальные метастазы_нет'] = db['Экстракраниальные метастазы_нет'].astype(int)
        # db['Активирующие мутации_есть'] = db['Активирующие мутации_есть'].astype(int)
        # db['Активирующие мутации_не известно'] = db['Активирующие мутации_не известно'].astype(int)
        # db['Активирующие мутации_нет'] = db['Активирующие мутации_нет'].astype(int)


        db['Прогрессия'] = pd.Categorical(db['Прогрессия'])
        self.class_names = dict(enumerate(db['Прогрессия'].cat.categories))
        db['Прогрессия'] = db['Прогрессия'].cat.codes

        scaler = StandardScaler()
        y = db.pop('Прогрессия')
        y = y.values.astype(np.float32)
        y = to_categorical(y, num_classes=self.n_classes)

        x = db.values.astype(np.float32)

        x_train, x_test, y_train, y_test = train_test_split(x, y, train_size=0.8, random_state=1)
        x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, train_size=0.8, random_state=1)
        # smote = SMOTE(random_state=42)
        # x_train_resampled, y_train_resampled = smote.fit_resample(x_train, y_train)
        return np.array(x_train), np.array(y_train), np.array(x_val), np.array(y_val), np.array(x_test), np.array(y_test)


        # db = self.data.dropna(axis=1, how='all')
        # db = db.dropna(axis=0)
        # irrelevant_columns = ['dendrite_type', 'neurotransmitter', 'reporter_status', 'layer', 'file_name']
        # db = db.drop([x for x in irrelevant_columns if x in db.columns], axis=1, errors='ignore')
        # db['transgenic_line'] = pd.Categorical(db['transgenic_line'])
        # self.class_names = dict(enumerate(db['transgenic_line'].cat.categories))
        # db['transgenic_line'] = db['transgenic_line'].cat.codes
        # scaler = StandardScaler()
        # y = db.pop('transgenic_line')
        # y = y.values.astype(np.float32)
        # y = to_categorical(y, num_classes=self.n_classes)
        # x = db.values.astype(np.float32)
        # x = scaler.fit_transform(x)
        # x_train, x_test, y_train, y_test = train_test_split(x, y, train_size=0.8, random_state=1)
        # x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, train_size=0.8, random_state=1)
        # return x_train, y_train, x_val, y_val, x_test, y_test


    def _create_metadata(self) -> DataSet_meta:
        """
        :return: metadata supported by the locally sparse model.
        """
        dataset = DataSet_meta(**{'_data': self.x_train, '_labels': self.y_train, '_meta': self.y_train,
                                  '_valid_data': self.x_val, '_valid_labels': self.y_val, '_valid_meta': self.y_val,
                                  '_test_data': self.x_test, '_test_labels': self.y_test, '_test_meta': self.y_test})
        return dataset

    def create_model(self, display_step: int, feature_selection: bool):
        """
        :param display_step: integer, number of epochs to output info.
        :param feature_selection: bool, if using the gating net.
        :return: dict of model parameters.
        """
        self.model_params = {"input_node": self.x_train.shape[1],
                             "output_node": self.n_classes,
                             "feature_selection": feature_selection,
                             "activation_gating": 'tanh',
                             "display_step": display_step}
        self.training_params = {'batch_size': self.x_train.shape[0]}

    def __objective(self, trial) -> float:
        """
        :param trial: a process of evaluating an objective function using optuna.
        :return: accuracy for the trial.
        """
        self.model_params['hidden_layers_node'] = trial.suggest_categorical("hidden_layers_node", [[70, 20],
                                                                             [50, 10],
                                                                             [40, 20, 10],
                                                                             [100, 20],
                                                                             [50, 20, 10], [10, 10, 10], [10, 5]])
        self.model_params['gating_net_hidden_layers_node'] = trial.suggest_categorical("gating_net_hidden_layers_node",
                                                                                       [[4, 4], [2, 2], [8], [20, 10],
                                                                                        [2, 2, 2],
                                                                                        [8, 2],])
        self.model_params['activation_pred'] = trial.suggest_categorical("activation_pred",
                                                                         ['relu', 'l_relu', 'sigmoid', 'tanh'])
        self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 0.01)
        self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.01)
        self.training_params['num_epoch'] = trial.suggest_categorical('num_epoch', [200, 500, 1000, 1500, 2000])

        self.model = Model(**self.model_params, batch_normalization=False)
        _, _, _, _ = self.model.train(dataset=self._create_metadata(), **self.training_params)

        y_pred = self.model.test(self.x_test)
        y_true = np.argmax(self.y_test, axis=1)
        accuracy = accuracy_score(y_true, y_pred)
        matrix = confusion_matrix(y_true, y_pred)
        print(matrix)
        return accuracy

    def __callback(self, study, trial) -> None:
        """
        :param study: study of the optuna framework.
        :param trial: specific trial of the optuna optimization.
        """
        if study.best_trial == trial:
            self.best_model = self.model

    def optimize(self, n_trials: int, n_jobs: int = 1) -> None:
        """
        :param n_trials: number of optimization trials.
        :param n_jobs: maximum number of concurrently running workers.
        :return: best m
        """
        study = optuna.create_study(study_name='lspin', direction='maximize')
        study.optimize(func=self.__objective, n_trials=n_trials, n_jobs=n_jobs, callbacks=[self.__callback])
        best_pred_arch = study.best_params['hidden_layers_node']
        best_gate_arch = study.best_params['gating_net_hidden_layers_node']
        best_activ_pred = study.best_params['activation_pred']
        best_lam = study.best_params['lam']
        best_lr = study.best_params['learning_rate']
        best_epoch = study.best_params['num_epoch']
        y_pred = self.best_model.test(self.x_test)
        accuracy = accuracy_score(np.argmax(self.y_test, axis=1), y_pred)
        f1 = f1_score(np.argmax(self.y_test, axis=1), y_pred, average='weighted')
        precision = precision_score(np.argmax(self.y_test, axis=1), y_pred, average='weighted')
        recall = recall_score(np.argmax(self.y_test, axis=1), y_pred, average='weighted')
        print("Trial Finished*************")
        print("Best model's prediction architecture: {}".format(best_pred_arch))
        print("Best model's gating architecture: {}".format(best_gate_arch))
        print("Best model's prediction activation function: {}".format(best_activ_pred))
        print("Best model's lambda: {}".format(best_lam))
        print("Best model's learning rate: {}".format(best_lr))
        print("Best model's num of epochs: {}".format(best_epoch))
        print("Test accuracy : {}".format(accuracy))
        print("Test F1 : {}".format(f1))
        print("Test precision : {}".format(precision))
        print("Test recall : {}".format(recall))

        with open(os.path.join(results_path, 'hyperparameters.txt'), "w") as file:
            file.write(
                "prediction architecture: {}\n"
                "gating architecture: {}\n"
                "prediction activation function: {}\n"
                "lambda: {}\n"
                "learning rate: {}\n"
                "number of epochs: {}\n"
                "Accuracy: {}\n"
                "F1: {}\n"
                "precision: {}\n"
                "recall: {}\n".format(best_pred_arch, best_gate_arch, best_activ_pred, best_lam,
                                      best_lr, best_epoch, accuracy, f1, precision, recall))

    def get_results(self) -> None:
        """
        plot the gate feature selection for each label in the data and confusion matrix.
        """
        # plot the gate feature selection matrix
        gate_matrix = []
        test_labels = np.argmax(self.y_test, axis=1)
        for i in range(self.n_classes):
            label_data = np.empty((0, self.x_test.shape[1]))
            for j in range(self.x_test.shape[0]):
                if test_labels[j] == i:
                    label_data = np.vstack([label_data, self.x_test[j, :]])

            gate_matrix.append(self.best_model.get_prob_alpha(label_data))
            plt.figure()
            sns.clustermap(gate_matrix[i], vmin=0, vmax=1, cbar_pos=None)
            plt.xlabel('Features')
            plt.ylabel('Samples')
            plt.subplots_adjust(top=0.95, bottom=0.1, right=0.9)
            plt.suptitle("Label: {}".format(self.class_names[i], fontsize=16))
            plt.draw()
            plt.savefig(results_path + "/gate_matrix_" + str(self.class_names[i]) + ".png")

        plt.figure(figsize=(2, 4))
        sns.clustermap(np.array([[0, 0], [0, 0]]), vmin=0, vmax=1, cbar_pos=(.01, .2, .03, .4))
        plt.draw()
        plt.savefig(results_path + "/cbar.png")

        # plot the confusion matrix
        y_pred = self.best_model.test(self.x_test)
        y_true = np.argmax(self.y_test, axis=1)

        def reverse_labels(tup: tuple) -> list:
            """
            :param tup: tuple of label.
            :return: names of labels.
            """
            return [self.class_names[x] for x in tup]

        y_true_labeled, y_pred_labeled = reverse_labels(tuple(y_true)), reverse_labels(tuple(y_pred))
        matrix = confusion_matrix(y_true_labeled, y_pred_labeled)
        df_cm = pd.DataFrame(matrix, columns=np.unique(y_true_labeled), index=np.unique(y_true_labeled))
        # df_cm.index.name = 'Actual'
        # df_cm.columns.name = 'Predicted'
        plt.figure()
        cmap = sns.cubehelix_palette(light=0.9, as_cmap=True)
        cm_normalized = df_cm.div(df_cm.sum(axis=0), axis=1)
        sns.heatmap(cm_normalized, cbar=False, annot=True, cmap=cmap, square=True, fmt='.1%', annot_kws={'size': 10})
        plt.title('LSPIN Classification')
        plt.tight_layout()
        plt.draw()
        plt.savefig(results_path + "/lspin_results.png")
        plt.show()

    def save_model(self):
        """
        save the best model to path.
        """
        self.best_model.save(model_dir=results_path+'/model')


def load_model():
    tf.compat.v1.reset_default_graph()
    v1 = tf.compat.v1.Variable(tf.compat.v1.constant(0.1, shape=[2]), name="v1")
    v2 = tf.compat.v1.Variable(tf.compat.v1.constant(0.2, shape=[2]), name="v2")
    saver = tf.compat.v1.train.import_meta_graph(results_path + '/model/model.ckpt.meta')
    with tf.compat.v1.Session() as sess:
        saver.restore(sess, results_path + '/model/model.ckpt')
        print("Model restored")

In [ ]:
import warnings
warnings.filterwarnings("ignore", category=UserWarning, module="optuna.distributions")
warnings.filterwarnings("ignore", category=FutureWarning, module="optuna.distributions")

In [ ]:
device = get_device()
device

Num GPUs Available:  1
Name: /physical_device:GPU:0   Type: GPU
Num CPUs Available:  1
Name: /physical_device:CPU:0   Type: CPU
Enter device (such as /device:GPU:0 or /device:CPU:0): GPU: 0


'GPU: 0'

In [ ]:
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()

In [ ]:
with tf.device(device):
  clf = LocallySparse(data=data_norm, n_classes=2)
  clf.create_model(display_step=300, feature_selection=True)
  clf.optimize(n_trials=250)
  clf.get_results()
  clf.save_model()

[I 2025-05-31 10:57:47,371] A new study created in memory with name: lspin
<ipython-input-32-3ed09c44e2f5>:111: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 0.01)
<ipython-input-32-3ed09c44e2f5>:112: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.01)


num_samples : 470
Epoch: 300 train loss=0.700492978 valid loss= 0.700493455 valid acc= 0.474576265
Epoch: 600 train loss=0.700493693 valid loss= 0.700490415 valid acc= 0.474576265
Epoch: 900 train loss=0.700487137 valid loss= 0.700488269 valid acc= 0.474576265


[I 2025-05-31 10:57:54,042] Trial 0 finished with value: 0.5202702702702703 and parameters: {'hidden_layers_node': [10, 10, 10], 'gating_net_hidden_layers_node': [2, 2, 2], 'activation_pred': 'l_relu', 'lam': 0.008730775417923308, 'learning_rate': 0.006730821735420806, 'num_epoch': 1000}. Best is trial 0 with value: 0.5202702702702703.


Optimization Finished!
test loss: 0.7004836201667786, test acc: 0.5202702879905701
[[ 0 71]
 [ 0 77]]


<ipython-input-32-3ed09c44e2f5>:111: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 0.01)
<ipython-input-32-3ed09c44e2f5>:112: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.01)


...

<ipython-input-32-3ed09c44e2f5>:111: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 0.01)
<ipython-input-32-3ed09c44e2f5>:112: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.01)


num_samples : 470
Epoch: 300 train loss=0.698616982 valid loss= 0.700603604 valid acc= 0.483050853
Epoch: 600 train loss=0.697732508 valid loss= 0.699759960 valid acc= 0.491525412
Epoch: 900 train loss=0.695187151 valid loss= 0.698891342 valid acc= 0.525423706


[I 2025-05-31 11:25:23,120] Trial 249 finished with value: 0.6081081081081081 and parameters: {'hidden_layers_node': [70, 20], 'gating_net_hidden_layers_node': [8], 'activation_pred': 'tanh', 'lam': 0.007895208748770413, 'learning_rate': 0.006625711428490395, 'num_epoch': 1000}. Best is trial 94 with value: 0.6891891891891891.


Optimization Finished!
test loss: 0.695260763168335, test acc: 0.6081081032752991
[[35 36]
 [22 55]]
Trial Finished*************
Best model's prediction architecture: [70, 20]
Best model's gating architecture: [8]
Best model's prediction activation function: tanh
Best model's lambda: 0.00786889347133018
Best model's learning rate: 0.008455502961246664
Best model's num of epochs: 1000
Test accuracy : 0.6891891891891891
Test F1 : 0.6893027273849192
Test precision : 0.690423300012341
Test recall : 0.6891891891891891


FileNotFoundError: [Errno 2] No such file or directory: '/content/results/hyperparameters.txt'

In [ ]:
data_norm

Число очагов  Объем очагов  Число фракций  Индекс Карновского  ОВГМ  \
0        0.047619      0.177158            0.0            0.833333     1   
1        0.380952      0.010791            0.0            0.833333     0   
2        0.095238      0.112410            0.0            0.833333     0   
3        0.047619      0.049685            0.6            0.833333     0   
4        0.666667      0.216052            0.0            0.333333     0   
..            ...           ...            ...                 ...   ...   
731      0.002905      0.056477            0.0            0.676833     0   
732      0.045841      0.061195            0.0            0.827109     0   
733      0.156686      0.228403            0.0            0.666667     0   
734      0.085760      0.232430            0.0            0.666667     0   
735      0.000000      0.204782            0.0            0.500000     0   

     Операция   Возраст  Время метастазирования  Время реагирования  КРР  \
0           0  0.421053                1.164881           -0.005626    0   
1           0  0.842105                1.143593            0.099859    0   
2           0  0.877193                1.000000            0.057665    0   
3           1  0.771930                0.712676           -0.015471    0   
4           0  0.508772                0.724363            0.019691    0   
..        ...       ...                     ...                 ...  ...   
731         0  0.490158                0.211182            0.088418    0   
732         0  0.414648                0.057650            0.011853    0   
733         0  0.583189                0.229784            0.000521    0   
734         0  0.611957                0.150926            0.008499    0   
735         0  0.614324                0.092412            0.047708    0   

     Меланома  НМРЛ  РМЖ  РП  Таргетная терапия  Химиотерапия  Без лечения  \
0           0     0    1   0                  0             0            0   
1           0     0    1   0                  0             1            0   
2           0     0    0   1                  1             0            0   
3           0     0    0   1                  0             0            0   
4           0     0    0   1                  0             0            0   
..        ...   ...  ...  ..                ...           ...          ...   
731         0     0    1   0                  0             0            0   
732         0     1    0   0                  0             1            0   
733         0     0    1   0                  1             0            0   
734         0     1    0   0                  0             1            0   
735         1     0    0   0                  0             0            0   

     Мужчина  
0          0  
1          0  
2          1  
3          0  
4          1  
..       ...  
731        0  
732        1  
733        0  
734        0  
735        1  

[736 rows x 18 columns]

In [ ]:
X_test

Число очагов  Объем очагов  Число фракций  Индекс Карновского  ОВГМ  \
0         0.0000      0.580660       0.000000                 0.5     0   
1         0.3750      0.794049       0.000000                 1.0     1   
2         0.0000      0.000000       0.000000                 1.0     1   
3         0.4375      0.269177       0.000000                 1.0     0   
4         0.0625      0.037192       0.000000                 1.0     0   
5         0.5000      0.639238       0.000000                 1.0     1   
6         0.6875      0.225941       0.000000                 0.5     1   
7         0.0000      0.420735       0.000000                 0.5     0   
8         0.1250      0.120874       0.000000                 1.0     0   
9         0.0000      0.325430       0.000000                 1.5     0   
10        0.5000      0.499303       0.000000                 1.0     0   
11        0.0625      0.239424       0.000000                 0.5     0   
12        1.0000      1.000000       0.000000                 1.0     0   
13        0.0625      0.037657       0.000000                 1.5     0   
14        0.0000      0.129707       0.000000                 0.5     0   
15        0.0000      0.277545       0.000000                 1.0     0   
16        0.0000      0.866109       0.000000                 0.5     0   
17        0.0000      0.406323       0.000000                 1.0     0   
18        0.3750      0.384472       0.000000                 0.0     0   
19        0.1250      0.056718       0.000000                 0.5     0   
20        0.4375      0.712227       0.000000                 1.0     0   
21        0.0000      0.403068       0.000000                 0.5     0   
22        0.0000      0.132497       0.333333                 1.0     0   
23        0.4375      0.516969       0.333333                 0.5     0   
24        0.8750      0.561599       0.333333                 1.5     0   
25        0.6875      0.380288       0.000000                 0.5     1   
26        0.5000      0.081358       0.333333                 0.5     0   
27        0.0625      0.192934       0.333333                 1.0     0   
28        0.0000      0.062762       0.333333                 1.0     0   
29        0.1250      0.148303       0.000000                 0.5     0   
30        0.2500      0.004649       0.000000                 1.5     0   
31        1.0000      0.184100       0.333333                 1.5     0   
32        0.5625      0.617387       0.000000                 1.0     0   
33        0.8750      0.557880       0.333333                 1.5     0   
34        0.0000      0.013947       0.000000                 1.5     0   
35        0.0625      0.518364       0.333333                 1.0     0   
36        0.5000      0.212924       0.333333                 1.5     1   
37        0.1250      0.992562       0.333333                 1.0     0   
38        0.0000      0.076244       0.000000                 1.0     1   
39        0.7500      0.859135       0.666667                 1.0     0   
40        0.3125      0.078568       1.000000                 1.0     0   
41        0.0000      0.183636       0.000000                 1.0     0   
42        0.7500      0.358903       0.000000                 1.5     0   
43        0.6875      0.809391       0.333333                 1.5     1   

    Операция   Возраст  Время метастазирования  Время реагирования  ID  КРР  \
0          0  0.611111                0.535470            0.011524   1    1   
1          1  0.185185                0.101514            0.331626   2    0   
2          0  0.722222               -0.025230            0.275288   3    0   
3          0  0.777778                0.303057            0.008963   4    0   
4          0  0.851852                0.106857            0.007682   5    0   
5          0  0.481481                0.214604            0.361076   6    0   
6          0  0.740741                0.051054           -0.003841   7    1

In [ ]:
y = data_norm.pop('Прогрессия')
y = y.values.astype(np.float32)
y = to_categorical(y, num_classes=2)
x = data_norm.values.astype(np.float32)

x_train, x_test, y_train, y_test = train_test_split(x, y, train_size=0.8, random_state=1)
x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, train_size=0.8, random_state=1)

data_set_train = DataSet_meta(**{'_data': np.array(x_train), '_labels': np.array(y_train), '_meta': np.array(y_train),
                                  '_valid_data': np.array(x_val), '_valid_labels': np.array(y_val), '_valid_meta': np.array(y_val),
                                  '_test_data': np.array(x_test), '_test_labels': np.array(y_test), '_test_meta': np.array(y_test)})

In [ ]:
model_params = {"input_node": x_train.shape[1],
                             "output_node": 2,
                             "feature_selection": True,
                             "activation_gating": 'tanh',
                             "display_step": 100}
training_params = {'batch_size': x_train.shape[0]}

In [ ]:
model_params['hidden_layers_node'] = [100, 20]
model_params['gating_net_hidden_layers_node'] = [8]
model_params['activation_pred'] = 'tanh'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.006395469426059615
training_params['lr'] = 0.005318699775800981
training_params['num_epoch'] = 1200
 # [200, 500, 1000, 1500, 2000])

In [ ]:
model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

Best model perform:
{'hidden_layers_node': [50, 10], 'gating_net_hidden_layers_node': [8], 'activation_pred': 'l_relu', 'lam': 0.014250322021561568, 'learning_rate': 0.05143530982331898, 'num_epoch': 2000} -> 0.81 accuracy om LB Kaggle Public


In [ ]:
# {'hidden_layers_node': [50, 10], 'gating_net_hidden_layers_node': [8], 'activation_pred': 'l_relu', 'lam': 0.014250322021561568, 'learning_rate': 0.05143530982331898, 'num_epoch': 2000}
# 0,81
model_params['hidden_layers_node'] = [50, 10]
model_params['gating_net_hidden_layers_node'] = [8]
model_params['activation_pred'] = 'l_relu'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.014250322021561568
training_params['lr'] = 0.05143530982331898
training_params['num_epoch'] = 5000
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.704762816 valid loss= 0.704317093 valid acc= 0.525423706
Epoch: 200 train loss=0.704059124 valid loss= 0.704209089 valid acc= 0.542372882
Epoch: 300 train loss=0.703871369 valid loss= 0.704033792 valid acc= 0.584745765
Epoch: 400 train loss=0.703844428 valid loss= 0.703769863 valid acc= 0.610169470
Epoch: 500 train loss=0.703030944 valid loss= 0.703371882 valid acc= 0.610169470
Epoch: 600 train loss=0.702589571 valid loss= 0.702908158 valid acc= 0.610169470
Epoch: 700 train loss=0.701739669 valid loss= 0.702261627 valid acc= 0.627118647
Epoch: 800 train loss=0.700896084 valid loss= 0.701462328 valid acc= 0.652542353
Epoch: 900 train loss=0.701099992 valid loss= 0.700368762 valid acc= 0.652542353
Epoch: 1000 train loss=0.698989511 valid loss= 0.698782623 valid acc= 0.652542353
Epoch: 1100 train loss=0.693792999 valid loss= 0.696459055 valid acc= 0.652542353
Epoch: 1200 train loss=0.689481974 valid loss= 0.693106174 valid acc= 0.652542353
Epoch: 

([],
 [np.float32(0.70495427),
  np.float32(0.7048289),
  np.float32(0.7048873),
  np.float32(0.7047034),
  np.float32(0.7049096),
  np.float32(0.7046392),
  np.float32(0.70499957),
  np.float32(0.70463324),
  np.float32(0.70448864),
  np.float32(0.70460075),
  np.float32(0.70450187),
  np.float32(0.70463127),
  np.float32(0.7047009),
  np.float32(0.7047933),
  np.float32(0.7046933),
  np.float32(0.70475584),
  np.float32(0.70456606),
  np.float32(0.7045903),
  np.float32(0.7048317),
  np.float32(0.7048801),
  np.float32(0.70494455),
  np.float32(0.7047731),
  np.float32(0.70456666),
  np.float32(0.7047855),
  np.float32(0.704921),
  np.float32(0.7047675),
  np.float32(0.70487475),
  np.float32(0.70461345),
  np.float32(0.70442307),
  np.float32(0.70454),
  np.float32(0.7046771),
  np.float32(0.70440274),
  np.float32(0.70467013),
  np.float32(0.7045778),
  np.float32(0.7047702),
  np.float32(0.7045736),
  np.float32(0.7048251),
  np.float32(0.7043382),
  np.float32(0.7045803),
  np.fl

In [ ]:
# {'hidden_layers_node': [50, 10], 'gating_net_hidden_layers_node': [4, 4], 'activation_pred': 'l_relu', 'lam': 0.01766118164219442, 'learning_rate': 0.04476948942215, 'num_epoch': 2000}.
model_params['hidden_layers_node'] = [50, 10]
model_params['gating_net_hidden_layers_node'] = [4, 4]
model_params['activation_pred'] = 'l_relu'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.01766118164219442
training_params['lr'] = 0.04476948942215
training_params['num_epoch'] = 2000
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.707655072 valid loss= 0.707942188 valid acc= 0.457627118
Epoch: 200 train loss=0.707102239 valid loss= 0.707674682 valid acc= 0.542372882
Epoch: 300 train loss=0.706691861 valid loss= 0.707428336 valid acc= 0.525423706
Epoch: 400 train loss=0.705897927 valid loss= 0.707111418 valid acc= 0.525423706
Epoch: 500 train loss=0.705398083 valid loss= 0.706664681 valid acc= 0.533898294
Epoch: 600 train loss=0.704123557 valid loss= 0.706046581 valid acc= 0.542372882
Epoch: 700 train loss=0.703598380 valid loss= 0.705230951 valid acc= 0.559322059
Epoch: 800 train loss=0.701794028 valid loss= 0.704065919 valid acc= 0.567796588
Epoch: 900 train loss=0.702377856 valid loss= 0.702618837 valid acc= 0.576271176
Epoch: 1000 train loss=0.697655201 valid loss= 0.700488865 valid acc= 0.584745765
Epoch: 1100 train loss=0.694034994 valid loss= 0.697362781 valid acc= 0.584745765
Epoch: 1200 train loss=0.688949645 valid loss= 0.692870796 valid acc= 0.593220353
Epoch: 

([],
 [np.float32(0.7075953),
  np.float32(0.70770967),
  np.float32(0.7076346),
  np.float32(0.70757705),
  np.float32(0.7077374),
  np.float32(0.70738727),
  np.float32(0.7075048),
  np.float32(0.70762616),
  np.float32(0.70752794),
  np.float32(0.70740324),
  np.float32(0.70757407),
  np.float32(0.70751697),
  np.float32(0.7074146),
  np.float32(0.7076819),
  np.float32(0.70764536),
  np.float32(0.707643),
  np.float32(0.70757693),
  np.float32(0.70762354),
  np.float32(0.7073251),
  np.float32(0.70755804),
  np.float32(0.70734525),
  np.float32(0.70760083),
  np.float32(0.70763135),
  np.float32(0.70759845),
  np.float32(0.7075607),
  np.float32(0.7076492),
  np.float32(0.70761985),
  np.float32(0.7075178),
  np.float32(0.70752794),
  np.float32(0.7076242),
  np.float32(0.70751864),
  np.float32(0.70761114),
  np.float32(0.7075225),
  np.float32(0.70746773),
  np.float32(0.70749927),
  np.float32(0.707544),
  np.float32(0.7074887),
  np.float32(0.70737946),
  np.float32(0.7075659),

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_m.csv', index=False)

Best model perform:
{'hidden_layers_node': [100, 100, 50, 10]], 'gating_net_hidden_layers_node': [20, 10], 'activation_pred': 'l_relu', 'lam': 0.014250322021561568, 'learning_rate': 0.05143530982331898, 'num_epoch': 30000} -> 0.77 accuracy om LB Kaggle Public


In [ ]:
# {'hidden_layers_node': [100, 100, 50, 10]], 'gating_net_hidden_layers_node': [20, 10], 'activation_pred': 'l_relu', 'lam': 0.014250322021561568, 'learning_rate': 0.05143530982331898, 'num_epoch': 30000}
# 0,77
model_params['hidden_layers_node'] = [100, 100, 50, 10]
model_params['gating_net_hidden_layers_node'] = [20, 10]
model_params['activation_pred'] = 'l_relu'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.014250322021561568
training_params['lr'] = 0.05143530982331898
training_params['num_epoch'] = 30000
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.704995990 valid loss= 0.705175161 valid acc= 0.474576265
Epoch: 200 train loss=0.704943359 valid loss= 0.705142915 valid acc= 0.474576265
Epoch: 300 train loss=0.704877257 valid loss= 0.705119729 valid acc= 0.474576265
Epoch: 400 train loss=0.704793394 valid loss= 0.705088258 valid acc= 0.474576265
Epoch: 500 train loss=0.704714239 valid loss= 0.705050766 valid acc= 0.474576265
Epoch: 600 train loss=0.704632044 valid loss= 0.705018938 valid acc= 0.474576265
Epoch: 700 train loss=0.704584420 valid loss= 0.704981685 valid acc= 0.474576265
Epoch: 800 train loss=0.704358518 valid loss= 0.704952061 valid acc= 0.474576265
Epoch: 900 train loss=0.704222262 valid loss= 0.704872727 valid acc= 0.474576265
Epoch: 1000 train loss=0.704366148 valid loss= 0.704817593 valid acc= 0.474576265
Epoch: 1100 train loss=0.704134643 valid loss= 0.704716265 valid acc= 0.474576265
Epoch: 1200 train loss=0.703758359 valid loss= 0.704634190 valid acc= 0.474576265
Epoch: 

([],
 [np.float32(0.70504445),
  np.float32(0.7050969),
  np.float32(0.7051126),
  np.float32(0.7050478),
  np.float32(0.7051143),
  np.float32(0.7051105),
  np.float32(0.7050807),
  np.float32(0.7051031),
  np.float32(0.7050567),
  np.float32(0.705068),
  np.float32(0.70504206),
  np.float32(0.7050362),
  np.float32(0.7051344),
  np.float32(0.7050577),
  np.float32(0.70509946),
  np.float32(0.7051251),
  np.float32(0.705027),
  np.float32(0.70507973),
  np.float32(0.7050959),
  np.float32(0.7050995),
  np.float32(0.70504755),
  np.float32(0.7050638),
  np.float32(0.7050325),
  np.float32(0.70498306),
  np.float32(0.7050366),
  np.float32(0.70504797),
  np.float32(0.70503664),
  np.float32(0.70502555),
  np.float32(0.7050593),
  np.float32(0.70508194),
  np.float32(0.7050073),
  np.float32(0.7050866),
  np.float32(0.7049872),
  np.float32(0.7050121),
  np.float32(0.70497674),
  np.float32(0.70499533),
  np.float32(0.7050809),
  np.float32(0.70506173),
  np.float32(0.7050469),
  np.floa

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_99.csv', index=False)

In [ ]:
model_params['hidden_layers_node'] = [50, 20]
model_params['gating_net_hidden_layers_node'] = [18]
model_params['activation_pred'] = 'l_relu'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.014250322021561568
training_params['lr'] = 0.05143530982331898
training_params['num_epoch'] = 4000
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.705278456 valid loss= 0.705350876 valid acc= 0.491525412
Epoch: 200 train loss=0.705270052 valid loss= 0.705320954 valid acc= 0.483050853
Epoch: 300 train loss=0.705206037 valid loss= 0.705279946 valid acc= 0.474576265
Epoch: 400 train loss=0.705112636 valid loss= 0.705233753 valid acc= 0.474576265
Epoch: 500 train loss=0.705059946 valid loss= 0.705186248 valid acc= 0.474576265
Epoch: 600 train loss=0.705082655 valid loss= 0.705136836 valid acc= 0.483050853
Epoch: 700 train loss=0.704894423 valid loss= 0.705084383 valid acc= 0.483050853
Epoch: 800 train loss=0.704942942 valid loss= 0.705031216 valid acc= 0.483050853
Epoch: 900 train loss=0.704915822 valid loss= 0.704979837 valid acc= 0.500000000
Epoch: 1000 train loss=0.704835534 valid loss= 0.704927087 valid acc= 0.508474588
Epoch: 1100 train loss=0.704779983 valid loss= 0.704872370 valid acc= 0.508474588
Epoch: 1200 train loss=0.704770267 valid loss= 0.704818308 valid acc= 0.508474588
Epoch: 

([],
 [np.float32(0.70592177),
  np.float32(0.7061736),
  np.float32(0.70564663),
  np.float32(0.7061659),
  np.float32(0.70592624),
  np.float32(0.705752),
  np.float32(0.7058421),
  np.float32(0.706003),
  np.float32(0.7058113),
  np.float32(0.70584303),
  np.float32(0.70623726),
  np.float32(0.7059033),
  np.float32(0.7056329),
  np.float32(0.7058903),
  np.float32(0.70560515),
  np.float32(0.7057361),
  np.float32(0.7057158),
  np.float32(0.7054287),
  np.float32(0.7056582),
  np.float32(0.70538557),
  np.float32(0.70554745),
  np.float32(0.7055647),
  np.float32(0.70538515),
  np.float32(0.7054142),
  np.float32(0.7054043),
  np.float32(0.70541626),
  np.float32(0.70541495),
  np.float32(0.7054206),
  np.float32(0.70539385),
  np.float32(0.7053922),
  np.float32(0.70540476),
  np.float32(0.7053941),
  np.float32(0.7053543),
  np.float32(0.7053876),
  np.float32(0.7054487),
  np.float32(0.70543003),
  np.float32(0.7055604),
  np.float32(0.7054831),
  np.float32(0.70528096),
  np.fl

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_5.csv', index=False)

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_5.csv', index=False)

In [ ]:
# {'hidden_layers_node': [50, 10], 'gating_net_hidden_layers_node': [8], 'activation_pred': 'l_relu', 'lam': 0.014250322021561568, 'learning_rate': 0.05143530982331898, 'num_epoch': 2000}
model_params['hidden_layers_node'] = [50, 10]
model_params['gating_net_hidden_layers_node'] = [4, 4]
model_params['activation_pred'] = 'l_relu'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.014250322021561568
training_params['lr'] = 0.05143530982331898
training_params['num_epoch'] = 3500
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.705134034 valid loss= 0.705162704 valid acc= 0.466101706
Epoch: 200 train loss=0.705082119 valid loss= 0.705141246 valid acc= 0.440677971
Epoch: 300 train loss=0.705068707 valid loss= 0.705122292 valid acc= 0.457627118
Epoch: 400 train loss=0.704975665 valid loss= 0.705093920 valid acc= 0.457627118
Epoch: 500 train loss=0.705010474 valid loss= 0.705072045 valid acc= 0.449152529
Epoch: 600 train loss=0.705000281 valid loss= 0.705048740 valid acc= 0.466101706
Epoch: 700 train loss=0.704919815 valid loss= 0.705023110 valid acc= 0.508474588
Epoch: 800 train loss=0.704948425 valid loss= 0.705003500 valid acc= 0.508474588
Epoch: 900 train loss=0.704921603 valid loss= 0.704980373 valid acc= 0.516949177
Epoch: 1000 train loss=0.704862177 valid loss= 0.704952180 valid acc= 0.525423706
Epoch: 1100 train loss=0.704880834 valid loss= 0.704930782 valid acc= 0.525423706
Epoch: 1200 train loss=0.704821467 valid loss= 0.704912901 valid acc= 0.516949177
Epoch: 

([],
 [np.float32(0.705188),
  np.float32(0.7051723),
  np.float32(0.70517665),
  np.float32(0.7051636),
  np.float32(0.70514995),
  np.float32(0.7051405),
  np.float32(0.70514256),
  np.float32(0.7051417),
  np.float32(0.70511),
  np.float32(0.7051555),
  np.float32(0.70515114),
  np.float32(0.70513505),
  np.float32(0.705154),
  np.float32(0.7051084),
  np.float32(0.7051344),
  np.float32(0.70510966),
  np.float32(0.70511836),
  np.float32(0.70509344),
  np.float32(0.7051181),
  np.float32(0.70513326),
  np.float32(0.7051441),
  np.float32(0.70516837),
  np.float32(0.70512336),
  np.float32(0.7051385),
  np.float32(0.7051192),
  np.float32(0.7050912),
  np.float32(0.70517206),
  np.float32(0.70509475),
  np.float32(0.7051327),
  np.float32(0.7051319),
  np.float32(0.70514494),
  np.float32(0.7051762),
  np.float32(0.70516527),
  np.float32(0.7050754),
  np.float32(0.7051141),
  np.float32(0.70513016),
  np.float32(0.7051712),
  np.float32(0.7051237),
  np.float32(0.7051077),
  np.flo

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_pred.csv', index=False)

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_pred.csv', index=False)

In [ ]:
# {'hidden_layers_node': [50, 10], 'gating_net_hidden_layers_node': [8], 'activation_pred': 'l_relu', 'lam': 0.014250322021561568, 'learning_rate': 0.05143530982331898, 'num_epoch': 2000}
model_params['hidden_layers_node'] = [50, 10]
model_params['gating_net_hidden_layers_node'] = [8]
model_params['activation_pred'] = 'l_relu'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.014250322021561568
training_params['lr'] = 0.05143530982331898
training_params['num_epoch'] = 4000
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.704918087 valid loss= 0.704695344 valid acc= 0.525423706
Epoch: 200 train loss=0.704556108 valid loss= 0.704524338 valid acc= 0.550847471
Epoch: 300 train loss=0.703994453 valid loss= 0.704330862 valid acc= 0.576271176
Epoch: 400 train loss=0.703954577 valid loss= 0.704108953 valid acc= 0.584745765
Epoch: 500 train loss=0.703467011 valid loss= 0.703739345 valid acc= 0.601694942
Epoch: 600 train loss=0.702607870 valid loss= 0.703256667 valid acc= 0.610169470
Epoch: 700 train loss=0.701302707 valid loss= 0.702538669 valid acc= 0.610169470
Epoch: 800 train loss=0.699726582 valid loss= 0.701425016 valid acc= 0.627118647
Epoch: 900 train loss=0.697340906 valid loss= 0.699706316 valid acc= 0.644067824
Epoch: 1000 train loss=0.695302367 valid loss= 0.697090626 valid acc= 0.644067824
Epoch: 1100 train loss=0.687514424 valid loss= 0.692840219 valid acc= 0.669491529
Epoch: 1200 train loss=0.680222094 valid loss= 0.685890377 valid acc= 0.669491529
Epoch: 

([],
 [np.float32(0.7049389),
  np.float32(0.70495033),
  np.float32(0.7049576),
  np.float32(0.704857),
  np.float32(0.7049937),
  np.float32(0.70480096),
  np.float32(0.70509475),
  np.float32(0.70476276),
  np.float32(0.7049216),
  np.float32(0.70496327),
  np.float32(0.705147),
  np.float32(0.70497173),
  np.float32(0.7050117),
  np.float32(0.7049967),
  np.float32(0.70500374),
  np.float32(0.7049321),
  np.float32(0.7049768),
  np.float32(0.7049173),
  np.float32(0.7047264),
  np.float32(0.7047314),
  np.float32(0.70490485),
  np.float32(0.70485234),
  np.float32(0.7047716),
  np.float32(0.7047747),
  np.float32(0.7047678),
  np.float32(0.70483387),
  np.float32(0.7048374),
  np.float32(0.70483595),
  np.float32(0.7048429),
  np.float32(0.70498097),
  np.float32(0.7049224),
  np.float32(0.7049235),
  np.float32(0.7049132),
  np.float32(0.70474494),
  np.float32(0.7049013),
  np.float32(0.70483506),
  np.float32(0.7047772),
  np.float32(0.7050575),
  np.float32(0.70480126),
  np.fl

In [ ]:
y_pred = model.test(X_test)
y_pred

array([0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target_pred.csv', index=False)

In [ ]:
model_params['hidden_layers_node'] = [100, 20]
model_params['gating_net_hidden_layers_node'] = [8]
model_params['activation_pred'] = 'tanh'
                                                                 #  ['relu', 'l_relu', 'sigmoid', 'tanh'])
model_params['lam'] = 0.006395469426059615
training_params['lr'] = 0.005318699775800981
training_params['num_epoch'] = 1500
 # [200, 500, 1000, 1500, 2000])

model = Model(**model_params, batch_normalization=False)
model.train(dataset=data_set_train, **training_params)

num_samples : 470
Epoch: 100 train loss=0.698629975 valid loss= 0.699419141 valid acc= 0.432203382
Epoch: 200 train loss=0.699028432 valid loss= 0.699174523 valid acc= 0.457627118
Epoch: 300 train loss=0.698324084 valid loss= 0.698940158 valid acc= 0.491525412
Epoch: 400 train loss=0.698044956 valid loss= 0.698708653 valid acc= 0.525423706
Epoch: 500 train loss=0.697421432 valid loss= 0.698482811 valid acc= 0.533898294
Epoch: 600 train loss=0.697038293 valid loss= 0.698263168 valid acc= 0.525423706
Epoch: 700 train loss=0.697125912 valid loss= 0.698037148 valid acc= 0.567796588
Epoch: 800 train loss=0.696520448 valid loss= 0.697815537 valid acc= 0.576271176
Epoch: 900 train loss=0.696191192 valid loss= 0.697586060 valid acc= 0.584745765
Epoch: 1000 train loss=0.696174026 valid loss= 0.697354734 valid acc= 0.601694942
Epoch: 1100 train loss=0.696347177 valid loss= 0.697115958 valid acc= 0.593220353
Epoch: 1200 train loss=0.695374727 valid loss= 0.696877062 valid acc= 0.601694942
Epoch: 

([],
 [np.float32(0.69954956),
  np.float32(0.69917274),
  np.float32(0.6990905),
  np.float32(0.6991325),
  np.float32(0.6992004),
  np.float32(0.69919443),
  np.float32(0.6994655),
  np.float32(0.69896436),
  np.float32(0.6992181),
  np.float32(0.6992997),
  np.float32(0.6988979),
  np.float32(0.6994402),
  np.float32(0.6989351),
  np.float32(0.6992416),
  np.float32(0.6988559),
  np.float32(0.6992679),
  np.float32(0.6991125),
  np.float32(0.6990583),
  np.float32(0.699381),
  np.float32(0.6992084),
  np.float32(0.69885147),
  np.float32(0.69893134),
  np.float32(0.6991084),
  np.float32(0.6984872),
  np.float32(0.6991724),
  np.float32(0.6990184),
  np.float32(0.69952494),
  np.float32(0.6985049),
  np.float32(0.6992908),
  np.float32(0.699076),
  np.float32(0.6988645),
  np.float32(0.69869286),
  np.float32(0.6990352),
  np.float32(0.6986487),
  np.float32(0.6990802),
  np.float32(0.69893396),
  np.float32(0.6991784),
  np.float32(0.69895333),
  np.float32(0.6988544),
  np.float32

In [ ]:
X_test

Число очагов  Объем очагов  Число фракций  Индекс Карновского  ОВГМ  \
0         0.0000      0.580660       0.000000                 0.5     0   
1         0.3750      0.794049       0.000000                 1.0     1   
2         0.0000      0.000000       0.000000                 1.0     1   
3         0.4375      0.269177       0.000000                 1.0     0   
4         0.0625      0.037192       0.000000                 1.0     0   
5         0.5000      0.639238       0.000000                 1.0     1   
6         0.6875      0.225941       0.000000                 0.5     1   
7         0.0000      0.420735       0.000000                 0.5     0   
8         0.1250      0.120874       0.000000                 1.0     0   
9         0.0000      0.325430       0.000000                 1.5     0   
10        0.5000      0.499303       0.000000                 1.0     0   
11        0.0625      0.239424       0.000000                 0.5     0   
12        1.0000      1.000000       0.000000                 1.0     0   
13        0.0625      0.037657       0.000000                 1.5     0   
14        0.0000      0.129707       0.000000                 0.5     0   
15        0.0000      0.277545       0.000000                 1.0     0   
16        0.0000      0.866109       0.000000                 0.5     0   
17        0.0000      0.406323       0.000000                 1.0     0   
18        0.3750      0.384472       0.000000                 0.0     0   
19        0.1250      0.056718       0.000000                 0.5     0   
20        0.4375      0.712227       0.000000                 1.0     0   
21        0.0000      0.403068       0.000000                 0.5     0   
22        0.0000      0.132497       0.333333                 1.0     0   
23        0.4375      0.516969       0.333333                 0.5     0   
24        0.8750      0.561599       0.333333                 1.5     0   
25        0.6875      0.380288       0.000000                 0.5     1   
26        0.5000      0.081358       0.333333                 0.5     0   
27        0.0625      0.192934       0.333333                 1.0     0   
28        0.0000      0.062762       0.333333                 1.0     0   
29        0.1250      0.148303       0.000000                 0.5     0   
30        0.2500      0.004649       0.000000                 1.5     0   
31        1.0000      0.184100       0.333333                 1.5     0   
32        0.5625      0.617387       0.000000                 1.0     0   
33        0.8750      0.557880       0.333333                 1.5     0   
34        0.0000      0.013947       0.000000                 1.5     0   
35        0.0625      0.518364       0.333333                 1.0     0   
36        0.5000      0.212924       0.333333                 1.5     1   
37        0.1250      0.992562       0.333333                 1.0     0   
38        0.0000      0.076244       0.000000                 1.0     1   
39        0.7500      0.859135       0.666667                 1.0     0   
40        0.3125      0.078568       1.000000                 1.0     0   
41        0.0000      0.183636       0.000000                 1.0     0   
42        0.7500      0.358903       0.000000                 1.5     0   
43        0.6875      0.809391       0.333333                 1.5     1   

    Операция   Возраст  Время метастазирования  Время реагирования  ID  КРР  \
0          0  0.611111                0.535470            0.011524   1    1   
1          1  0.185185                0.101514            0.331626   2    0   
2          0  0.722222               -0.025230            0.275288   3    0   
3          0  0.777778                0.303057            0.008963   4    0   
4          0  0.851852                0.106857            0.007682   5    0   
5          0  0.481481                0.214604            0.361076   6    0   
6          0  0.740741                0.051054           -0.003841   7    1

In [ ]:
pd.DataFrame(x_train)

0         1    2         3    4    5         6         7   \
0    0.238095  0.292941  0.0  0.666667  0.0  0.0  0.771930  0.030889   
1    0.190476  0.265288  0.0  0.833333  1.0  0.0  0.403509  0.262697   
2    0.095238  0.091951  0.0  0.666667  0.0  0.0  0.473684  0.196605   
3    0.000000  0.042403  0.0  0.571185  0.0  0.0  0.568897  0.138046   
4    0.388393  0.064365  0.0  0.763765  0.0  0.0  0.307253  0.128515   
..        ...       ...  ...       ...  ...  ...       ...       ...   
465  0.050052  0.045000  0.0  0.666667  0.0  0.0  0.825329  0.082639   
466  0.124583  0.114580  0.0  0.500000  0.0  1.0  0.496019  0.089225   
467  0.142857  0.193570  0.2  0.666667  0.0  0.0  0.771930  0.008627   
468  0.032685  0.166759  0.0  0.628534  0.0  1.0  0.586975  0.022551   
469  0.285714  0.119155  0.0  0.833333  0.0  1.0  0.298246  0.012801   

           8    9    10   11   12   13   14   15   16   17  
0    0.019691  0.0  0.0  1.0  0.0  0.0  0.0  1.0  0.0  1.0  
1    0.045007  0.0  0.0  0.0  1.0  0.0  0.0  1.0  0.0  0.0  
2    0.357243  0.0  0.0  0.0  1.0  0.0  0.0  1.0  0.0  0.0  
3    0.009831  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  
4    0.094698  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  
..        ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
465  0.042122  0.0  1.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  
466  1.283256  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  
467  0.047820  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  
468  0.387342  0.0  0.0  1.0  0.0  0.0  0.0  1.0  0.0  1.0  
469  0.140647  0.0  0.0  1.0  0.0  0.0  1.0  0.0  0.0  0.0  

[470 rows x 18 columns]

In [ ]:
id = X_test.pop('ID')

In [ ]:
y_pred = model.test(X_test)

In [ ]:
y_pred

array([1, 1, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1])

In [ ]:
pd.concat([id, pd.DataFrame(y_pred, columns=['Прогрессия'])], axis=1).to_csv('test_target.csv', index=False)

In [ ]:
with tf.device(device):
  clf = LocallySparse(data=new_trasngenic_data, n_classes=2)
  clf.create_model(display_step=250, feature_selection=True)
  clf.optimize(n_trials=250)
  clf.get_results()
  clf.save_model()

[I 2025-05-29 13:05:00,648] A new study created in memory with name: lspin
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [5, 5] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [100, 50, 10] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [50, 30, 20, 10] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribu

num_samples : 448
Epoch: 250 train loss=0.796393633 valid loss= 0.794670820 valid acc= 0.530973434


[I 2025-05-29 13:05:05,571] Trial 0 finished with value: 0.5035460992907801 and parameters: {'hidden_layers_node': [5, 5], 'gating_net_hidden_layers_node': [50, 50], 'activation_pred': 'l_relu', 'lam': 0.37473685186882427, 'learning_rate': 0.03919870150727051, 'num_epoch': 500}. Best is trial 0 with value: 0.5035460992907801.


Epoch: 500 train loss=0.775726140 valid loss= 0.775089025 valid acc= 0.495575219
Optimization Finished!
test loss: 0.7710863351821899, test acc: 0.5035461187362671
[[ 0 70]
 [ 0 71]]


/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [5, 5] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [100, 50, 10] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [50, 30, 20, 10] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent sto

...

/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [5, 5] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [100, 50, 10] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [50, 30, 20, 10] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.11/dist-packages/optuna/distributions.py:515: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent sto

num_samples : 448
Epoch: 250 train loss=0.902446985 valid loss= 0.903162122 valid acc= 0.522123873
Epoch: 500 train loss=0.899295747 valid loss= 0.900453806 valid acc= 0.513274312
Epoch: 750 train loss=0.897671402 valid loss= 0.897376776 valid acc= 0.486725658


[I 2025-05-29 13:32:09,667] Trial 249 finished with value: 0.574468085106383 and parameters: {'hidden_layers_node': [5, 5, 5], 'gating_net_hidden_layers_node': [18, 9], 'activation_pred': 'l_relu', 'lam': 0.2514696761169139, 'learning_rate': 0.005068616819665002, 'num_epoch': 1000}. Best is trial 218 with value: 0.5957446808510638.


Epoch: 1000 train loss=0.893089771 valid loss= 0.892476141 valid acc= 0.539822996
Optimization Finished!
test loss: 0.8891938328742981, test acc: 0.5744680762290955
[[58 12]
 [48 23]]
Trial Finished*************
Best model's prediction architecture: [50, 25, 10]
Best model's gating architecture: [8]
Best model's prediction activation function: l_relu
Best model's lambda: 0.21814266532244772
Best model's learning rate: 0.005049986000952147
Best model's num of epochs: 1000
Test accuracy : 0.5957446808510638
Test F1 : 0.5632498941190183
Test precision : 0.6397557583447199
Test recall : 0.5957446808510638


FileNotFoundError: [Errno 2] No such file or directory: '/content/results/lspin/hyperparameters.txt'

In [ ]:
class LocallySparse:
    """
    uses the LSPIN model to classify transgenic targeting in mouse data.
    """
    def __init__(self, data: pd.DataFrame, n_classes: int) -> None:
        """
        :param data: raw dataframe of neuronal recordings.
        :param n_classes: number of transgenic lines in the dataframe.
        """
        self.data = data
        self.n_classes = n_classes
        self.model, self.best_model = None, None
        self.model_params, self.training_params, self.class_names = {}, {}, {}
        self.x_train, self.y_train, self.x_val, self.y_val, self.x_test, self.y_test = self._preprocess_data()

    def _preprocess_data(self) -> tuple:
        """
        :param df: raw dataframe to be processed.
        :param n_classes: number of classes in the dataframe.
        :return: split into train, validation and test.
        """
        db = self.data.dropna(axis=1, how='all')
        db = db.dropna(axis=0)


        # irrelevant_columns = ['Онкологический диагноз'] #уже удалено
        # db = db.drop([x for x in irrelevant_columns if x in db.columns], axis=1, errors='ignore')

        db['Экстракраниальные метастазы_есть'] = db['Экстракраниальные метастазы_есть'].astype(int)
        db['Экстракраниальные метастазы_не известно'] = db['Экстракраниальные метастазы_не известно'].astype(int)
        db['Экстракраниальные метастазы_нет'] = db['Экстракраниальные метастазы_нет'].astype(int)
        db['Активирующие мутации_есть'] = db['Активирующие мутации_есть'].astype(int)
        db['Активирующие мутации_не известно'] = db['Активирующие мутации_не известно'].astype(int)
        db['Активирующие мутации_нет'] = db['Активирующие мутации_нет'].astype(int)


        db['Прогрессия'] = pd.Categorical(db['Прогрессия'])
        self.class_names = dict(enumerate(db['Прогрессия'].cat.categories))
        db['Прогрессия'] = db['Прогрессия'].cat.codes

        scaler = StandardScaler()
        y = db.pop('Прогрессия')
        y = y.values.astype(np.float32)
        y = to_categorical(y, num_classes=self.n_classes)

        x = db.values.astype(np.float32)

        x_train, x_test, y_train, y_test = train_test_split(x, y, train_size=0.8, random_state=1)
        x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, train_size=0.8, random_state=1)
        # smote = SMOTE(random_state=42)
        # x_train_resampled, y_train_resampled = smote.fit_resample(x_train, y_train)
        return np.array(x_train), np.array(y_train), np.array(x_val), np.array(y_val), np.array(x_test), np.array(y_test)


        # db = self.data.dropna(axis=1, how='all')
        # db = db.dropna(axis=0)
        # irrelevant_columns = ['dendrite_type', 'neurotransmitter', 'reporter_status', 'layer', 'file_name']
        # db = db.drop([x for x in irrelevant_columns if x in db.columns], axis=1, errors='ignore')
        # db['transgenic_line'] = pd.Categorical(db['transgenic_line'])
        # self.class_names = dict(enumerate(db['transgenic_line'].cat.categories))
        # db['transgenic_line'] = db['transgenic_line'].cat.codes
        # scaler = StandardScaler()
        # y = db.pop('transgenic_line')
        # y = y.values.astype(np.float32)
        # y = to_categorical(y, num_classes=self.n_classes)
        # x = db.values.astype(np.float32)
        # x = scaler.fit_transform(x)
        # x_train, x_test, y_train, y_test = train_test_split(x, y, train_size=0.8, random_state=1)
        # x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, train_size=0.8, random_state=1)
        # return x_train, y_train, x_val, y_val, x_test, y_test


    def _create_metadata(self) -> DataSet_meta:
        """
        :return: metadata supported by the locally sparse model.
        """
        dataset = DataSet_meta(**{'_data': self.x_train, '_labels': self.y_train, '_meta': self.y_train,
                                  '_valid_data': self.x_val, '_valid_labels': self.y_val, '_valid_meta': self.y_val,
                                  '_test_data': self.x_test, '_test_labels': self.y_test, '_test_meta': self.y_test})
        return dataset

    def create_model(self, display_step: int, feature_selection: bool):
        """
        :param display_step: integer, number of epochs to output info.
        :param feature_selection: bool, if using the gating net.
        :return: dict of model parameters.
        """
        self.model_params = {"input_node": self.x_train.shape[1],
                             "output_node": self.n_classes,
                             "feature_selection": feature_selection,
                             "activation_gating": 'tanh',
                             "display_step": display_step}
        self.training_params = {'batch_size': self.x_train.shape[0]}

    def __objective(self, trial) -> float:
        """
        :param trial: a process of evaluating an objective function using optuna.
        :return: accuracy for the trial.
        """
        self.model_params['hidden_layers_node'] = trial.suggest_categorical("hidden_layers_node", [[5, 5],
                                                                             [50, 20, 10],
                                                                             [30, 30, 20, 10],
                                                                             [20, 10, 5],
                                                                             [10, 10, 4], [10, 10],
                                                                             [10, 10, 10], [50, 10], [2, 2], [5, 3]])
        self.model_params['gating_net_hidden_layers_node'] = trial.suggest_categorical("gating_net_hidden_layers_node",
                                                                                       [[4, 4], [10], [4, 2, 2], [8], [2, 2, 2],
                                                                                        [6, 2],
                                                                                        [10, 4],
                                                                                        [4, 4, 4]])
        self.model_params['activation_pred'] = trial.suggest_categorical("activation_pred",
                                                                         ['relu', 'l_relu', 'sigmoid', 'tanh'])
        self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 1)
        self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.1)
        self.training_params['num_epoch'] = trial.suggest_categorical('num_epoch', [500, 1000, 1500, 2000])

        self.model = Model(**self.model_params, batch_normalization=False)
        _, _, _, _ = self.model.train(dataset=self._create_metadata(), **self.training_params)

        y_pred = self.model.test(self.x_test)
        y_true = np.argmax(self.y_test, axis=1)
        accuracy = accuracy_score(y_true, y_pred)
        matrix = confusion_matrix(y_true, y_pred)
        print(matrix)
        return accuracy

    def __callback(self, study, trial) -> None:
        """
        :param study: study of the optuna framework.
        :param trial: specific trial of the optuna optimization.
        """
        if study.best_trial == trial:
            self.best_model = self.model

    def optimize(self, n_trials: int, n_jobs: int = 1) -> None:
        """
        :param n_trials: number of optimization trials.
        :param n_jobs: maximum number of concurrently running workers.
        :return: best m
        """
        study = optuna.create_study(study_name='lspin', direction='maximize')
        study.optimize(func=self.__objective, n_trials=n_trials, n_jobs=n_jobs, callbacks=[self.__callback])
        best_pred_arch = study.best_params['hidden_layers_node']
        best_gate_arch = study.best_params['gating_net_hidden_layers_node']
        best_activ_pred = study.best_params['activation_pred']
        best_lam = study.best_params['lam']
        best_lr = study.best_params['learning_rate']
        best_epoch = study.best_params['num_epoch']
        y_pred = self.best_model.test(self.x_test)
        accuracy = accuracy_score(np.argmax(self.y_test, axis=1), y_pred)
        f1 = f1_score(np.argmax(self.y_test, axis=1), y_pred, average='weighted')
        precision = precision_score(np.argmax(self.y_test, axis=1), y_pred, average='weighted')
        recall = recall_score(np.argmax(self.y_test, axis=1), y_pred, average='weighted')
        print("Trial Finished*************")
        print("Best model's prediction architecture: {}".format(best_pred_arch))
        print("Best model's gating architecture: {}".format(best_gate_arch))
        print("Best model's prediction activation function: {}".format(best_activ_pred))
        print("Best model's lambda: {}".format(best_lam))
        print("Best model's learning rate: {}".format(best_lr))
        print("Best model's num of epochs: {}".format(best_epoch))
        print("Test accuracy : {}".format(accuracy))
        print("Test F1 : {}".format(f1))
        print("Test precision : {}".format(precision))
        print("Test recall : {}".format(recall))

        with open(os.path.join(results_path, 'hyperparameters.txt'), "w") as file:
            file.write(
                "prediction architecture: {}\n"
                "gating architecture: {}\n"
                "prediction activation function: {}\n"
                "lambda: {}\n"
                "learning rate: {}\n"
                "number of epochs: {}\n"
                "Accuracy: {}\n"
                "F1: {}\n"
                "precision: {}\n"
                "recall: {}\n".format(best_pred_arch, best_gate_arch, best_activ_pred, best_lam,
                                      best_lr, best_epoch, accuracy, f1, precision, recall))

    def get_results(self) -> None:
        """
        plot the gate feature selection for each label in the data and confusion matrix.
        """
        # plot the gate feature selection matrix
        gate_matrix = []
        test_labels = np.argmax(self.y_test, axis=1)
        for i in range(self.n_classes):
            label_data = np.empty((0, self.x_test.shape[1]))
            for j in range(self.x_test.shape[0]):
                if test_labels[j] == i:
                    label_data = np.vstack([label_data, self.x_test[j, :]])

            gate_matrix.append(self.best_model.get_prob_alpha(label_data))
            plt.figure()
            sns.clustermap(gate_matrix[i], vmi1n=0, vmax=1, cbar_pos=None)
            plt.xlabel('Features')
            plt.ylabel('Samples')
            plt.subplots_adjust(top=0.95, bottom=0.1, right=0.9)
            plt.suptitle("Label: {}".format(self.class_names[i], fontsize=16))
            plt.draw()
            plt.savefig(results_path + "/gate_matrix_" + str(self.class_names[i]) + ".png")

        plt.figure(figsize=(2, 4))
        sns.clustermap(np.array([[0, 0], [0, 0]]), vmin=0, vmax=1, cbar_pos=(.01, .2, .03, .4))
        plt.draw()
        plt.savefig(results_path + "/cbar.png")

        # plot the confusion matrix
        y_pred = self.best_model.test(self.x_test)
        y_true = np.argmax(self.y_test, axis=1)

        def reverse_labels(tup: tuple) -> list:
            """
            :param tup: tuple of label.
            :return: names of labels.
            """
            return [self.class_names[x] for x in tup]

        y_true_labeled, y_pred_labeled = reverse_labels(tuple(y_true)), reverse_labels(tuple(y_pred))
        matrix = confusion_matrix(y_true_labeled, y_pred_labeled)
        df_cm = pd.DataFrame(matrix, columns=np.unique(y_true_labeled), index=np.unique(y_true_labeled))
        # df_cm.index.name = 'Actual'
        # df_cm.columns.name = 'Predicted'
        plt.figure()
        cmap = sns.cubehelix_palette(light=0.9, as_cmap=True)
        cm_normalized = df_cm.div(df_cm.sum(axis=0), axis=1)
        sns.heatmap(cm_normalized, cbar=False, annot=True, cmap=cmap, square=True, fmt='.1%', annot_kws={'size': 10})
        plt.title('LSPIN Classification')
        plt.tight_layout()
        plt.draw()
        plt.savefig(results_path + "/lspin_results.png")
        plt.show()

    def save_model(self):
        """
        save the best model to path.
        """
        self.best_model.save(model_dir=results_path+'/model')


def load_model():
    tf.compat.v1.reset_default_graph()
    v1 = tf.compat.v1.Variable(tf.compat.v1.constant(0.1, shape=[2]), name="v1")
    v2 = tf.compat.v1.Variable(tf.compat.v1.constant(0.2, shape=[2]), name="v2")
    saver = tf.compat.v1.train.import_meta_graph(results_path + '/model/model.ckpt.meta')
    with tf.compat.v1.Session() as sess:
        saver.restore(sess, results_path + '/model/model.ckpt')
        print("Model restored")

In [ ]:
with tf.device(device):
  clf = LocallySparse(data=new_trasngenic_data, n_classes=2)
  clf.create_model(display_step=50, feature_selection=True)
  clf.optimize(n_trials=1000)
  clf.get_results()
  clf.save_model()

[I 2025-05-29 18:41:28,649] A new study created in memory with name: lspin
<ipython-input-17-f803361652f5>:113: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 1)
<ipython-input-17-f803361652f5>:114: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.1)
Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



num_samples : 448
Epoch: 50 train loss=0.716971517 valid loss= 0.715905964 valid acc= 0.486725658
Epoch: 100 train loss=0.715763569 valid loss= 0.715853512 valid acc= 0.469026536
Epoch: 150 train loss=0.715779603 valid loss= 0.715814114 valid acc= 0.495575219
Epoch: 200 train loss=0.716403604 valid loss= 0.715790272 valid acc= 0.504424751
Epoch: 250 train loss=0.716016054 valid loss= 0.715770602 valid acc= 0.495575219
Epoch: 300 train loss=0.715918601 valid loss= 0.715755761 valid acc= 0.495575219
Epoch: 350 train loss=0.715746999 valid loss= 0.715750217 valid acc= 0.486725658
Epoch: 400 train loss=0.715721905 valid loss= 0.715742588 valid acc= 0.442477882
Epoch: 450 train loss=0.715720415 valid loss= 0.715743303 valid acc= 0.451327443
Epoch: 500 train loss=0.715733171 valid loss= 0.715745211 valid acc= 0.451327443
Epoch: 550 train loss=0.715716422 valid loss= 0.715743840 valid acc= 0.451327443
Epoch: 600 train loss=0.715726674 valid loss= 0.715740323 valid acc= 0.451327443
Epoch: 650 

[I 2025-05-29 18:41:35,668] Trial 0 finished with value: 0.44680851063829785 and parameters: {'hidden_layers_node': [20, 10, 5], 'gating_net_hidden_layers_node': [4, 4, 4], 'activation_pred': 'relu', 'lam': 0.026865900409636795, 'learning_rate': 0.0012552032076294443, 'num_epoch': 1000}. Best is trial 0 with value: 0.44680851063829785.


Epoch: 950 train loss=0.715701580 valid loss= 0.715751827 valid acc= 0.451327443
Epoch: 1000 train loss=0.715704083 valid loss= 0.715753794 valid acc= 0.460177004
Optimization Finished!
test loss: 0.7157302498817444, test acc: 0.44680851697921753
[[34 36]
 [42 29]]


<ipython-input-17-f803361652f5>:113: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 1)
<ipython-input-17-f803361652f5>:114: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.1)


...

<ipython-input-17-f803361652f5>:113: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.model_params['lam'] = trial.suggest_loguniform('lam', 0.005, 1)
<ipython-input-17-f803361652f5>:114: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  self.training_params['lr'] = trial.suggest_loguniform('learning_rate', 0.00005, 0.1)


num_samples : 448
Epoch: 50 train loss=0.701093554 valid loss= 0.701611340 valid acc= 0.513274312
Epoch: 100 train loss=0.700952649 valid loss= 0.701736450 valid acc= 0.504424751
Epoch: 150 train loss=0.700889528 valid loss= 0.701889098 valid acc= 0.495575219
Epoch: 200 train loss=0.700752199 valid loss= 0.702051640 valid acc= 0.486725658
Epoch: 250 train loss=0.700747788 valid loss= 0.702174246 valid acc= 0.495575219
Epoch: 300 train loss=0.699571669 valid loss= 0.702272534 valid acc= 0.530973434
Epoch: 350 train loss=0.700513124 valid loss= 0.702333927 valid acc= 0.486725658
Epoch: 400 train loss=0.701169372 valid loss= 0.702354610 valid acc= 0.495575219
Epoch: 450 train loss=0.700871289 valid loss= 0.702457190 valid acc= 0.486725658
Epoch: 500 train loss=0.703651369 valid loss= 0.702420533 valid acc= 0.486725658
Epoch: 550 train loss=0.702726007 valid loss= 0.702334166 valid acc= 0.486725658
Epoch: 600 train loss=0.700984120 valid loss= 0.702426076 valid acc= 0.495575219
Epoch: 650 

[I 2025-05-29 21:13:32,371] Trial 999 finished with value: 0.5035460992907801 and parameters: {'hidden_layers_node': [20, 10, 5], 'gating_net_hidden_layers_node': [4, 4], 'activation_pred': 'l_relu', 'lam': 0.010175442023733675, 'learning_rate': 0.06357044609268524, 'num_epoch': 2000}. Best is trial 683 with value: 0.8226950354609929.


Epoch: 1950 train loss=0.700941920 valid loss= 0.702366054 valid acc= 0.486725658
Epoch: 2000 train loss=0.700403571 valid loss= 0.702689409 valid acc= 0.486725658
Optimization Finished!
test loss: 0.6984251737594604, test acc: 0.5035461187362671
[[66  4]
 [66  5]]
Trial Finished*************
Best model's prediction architecture: [50, 10]
Best model's gating architecture: [4, 4]
Best model's prediction activation function: l_relu
Best model's lambda: 0.01766118164219442
Best model's learning rate: 0.04476948942215
Best model's num of epochs: 2000
Test accuracy : 0.8226950354609929
Test F1 : 0.8225165255545857
Test precision : 0.82441435632925
Test recall : 0.8226950354609929


FileNotFoundError: [Errno 2] No such file or directory: '/content/results/hyperparameters.txt'

In [ ]:
clf

In [ ]:
# Best model's prediction architecture: [50, 25, 10]
# Best model's gating architecture: [8]
# Best model's prediction activation function: l_relu
# Best model's lambda: 0.21814266532244772
# Best model's learning rate: 0.005049986000952147
# Best model's num of epochs: 1000
# Test accuracy : 0.5957446808510638
# Test F1 : 0.5632498941190183
# Test precision : 0.6397557583447199
# Test recall : 0.5957446808510638